In [1]:

import numpy as np
import altair as alt
from tqdm import tqdm
import sys
sys.path.append('../../')
from Scanner.general_consts import *
# alt.data_transformers.enable('csv')

import csv
import json

import os

import pandas as pd
from scipy import integrate
import matplotlib.pyplot as plt
sys.path.insert(1, '/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch')

from resources.section_logtypes import section_logtypes
from resources.logtypes import logtypes
from experiment_manager import ExperimentManager
log_types_str = [f"{logtype[0].lower()}_{logtype[1]}" for logtype in logtypes]
# alt.renderers.enable('altair_saver', fmts=['png'])


In [2]:
# load savedsearches.conf
with open('/home/shouei/GreenSecurity-FirstExperiment/savedsearches.conf') as f:
    savedsearches = f.read().split('\n\n')
#find the window rules
window_rules = []
for savedsearch in savedsearches:
    if 'winevent' in savedsearch:
        window_rules.append(savedsearch)
# get the queries
queries = []
for window_rule in window_rules:
    query = window_rule.split('search = ')[1].split('\n')[0]
    queries.append(query)

In [15]:
queries

['`pingid` "result.message" = "*Device Paired*" | rex field=result.message "Device (Unp)?(P)?aired (?<device_extract>.+)" | eval src = coalesce(\'resources{}.ipaddress\',\'resources{}.devicemodel\'), user = upper(\'actors{}.name\'), reason = \'result.message\' | eval object=CASE(ISNOTNULL(\'resources{}.devicemodel\'),\'resources{}.devicemodel\',true(),device_extract) | eval action=CASE(match(\'result.message\',"Device Paired*"),"created",match(\'result.message\', "Device Unpaired*"),"deleted") | stats count min(_time) as firstTime, max(_time) as lastTime, values(reason) as reason by src,user,action,object | join type=outer user [| search `wineventlog_security` EventID IN(4723,4724) | eval PW_Change_Time = _time, user = upper(user) | fields user,src_user,EventID,PW_Change_Time] | eval timeDiffRaw = round(lastTime - PW_Change_Time) | eval timeDiff = replace(tostring(abs(timeDiffRaw) ,"duration"),"(\\d*)\\+*(\\d+):(\\d+):(\\d+)","\\2 hours \\3 minutes") | `security_content_ctime(firstTime

In [2]:
top_logtypes = pd.read_csv("../resources/top_logtypes.csv")
top_logtypes = top_logtypes.sort_values(by='count', ascending=False)[['source', "EventCode", 'count']].values.tolist()[:50]
top_logtypes

[['WinEventLog:Security', 4907, 424640],
 ['WinEventLog:Security', 4702, 155674],
 ['WinEventLog:Security', 4662, 103699],
 ['WinEventLog:Security', 5379, 70970],
 ['WinEventLog:Security', 4624, 63153],
 ['WinEventLog:Security', 4672, 60597],
 ['WinEventLog:Application', 1, 47341],
 ['WinEventLog:Security', 4799, 36889],
 ['WinEventLog:System', 44, 33430],
 ['WinEventLog:Security', 4634, 18160],
 ['WinEventLog:Security', 4648, 16376],
 ['WinEventLog:Security', 4735, 12716],
 ['WinEventLog:Application', 16384, 10334],
 ['WinEventLog:Security', 4625, 9828],
 ['WinEventLog:Application', 16394, 8583],
 ['WinEventLog:System', 7036, 5896],
 ['WinEventLog:System', 16, 5241],
 ['WinEventLog:Application', 0, 4509],
 ['WinEventLog:System', 108, 3994],
 ['WinEventLog:System', 1112, 3925],
 ['WinEventLog:System', 101, 3925],
 ['WinEventLog:Security', 5061, 3759],
 ['WinEventLog:System', 7040, 3669],
 ['WinEventLog:System', 1500, 3546],
 ['WinEventLog:System', 12, 2956],
 ['WinEventLog:System', 566

In [2]:

import os
import altair as alt
from toolz.curried import pipe


def json_dir(data, data_dir='altairdata'):
    os.makedirs(data_dir, exist_ok=True)
    return pipe(data, alt.to_json(filename=data_dir + '/{prefix}-{hash}.{extension}') )


alt.data_transformers.register('json_dir', json_dir)
alt.data_transformers.enable('json_dir')

DataTransformerRegistry.enable('json_dir')

In [3]:
# make new column of episode every num_of_steps steps
def add_episode_column(df, num_of_steps):
    df['episode'] = df.index // num_of_steps
    return df


In [4]:
env_names = []
dirs_names = os.listdir(f"/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__")
model_names = set()
reward_parameters = set()
learning_rates = set()
for dir in dirs_names:
    if not dir.__contains__('splunk') or int(dir.split("splunk-v")[1]) < 13:
        continue
    env_names.append(dir)
    for file in os.listdir(f"/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/{dir}"):

        if "__" not in file:
            continue
        info = file.split("__")
        model_name = info[0].split("_")[0]
        reward_parameter = '_'.join(info[0].split("_")[1:])
        lr = info[1]
        model_names.add(model_name)
        reward_parameters.add(reward_parameter)
        learning_rates.add(lr)

In [5]:
# # load the no agent 1200 episodes and make average between the no agent reward values and the reward values of the agent
# with open("/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/splunk-v12/no_agent_1200_04/26/2024:13:00:00/no_agent_reward_values_dict.json", "r") as f:
#     no_agent_reward_values_dict = json.load(f)

# with open("/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/splunk-v12/no_agent_1200_04/26/2024:13:00:00/reward_values_dict.json", "r") as f:
#     agent_reward_values_dict = json.load(f)
    
# duration_final_values = np.mean([no_agent_reward_values_dict['duration'], agent_reward_values_dict['duration']], axis=0)
# duration_final_values_std = np.std([no_agent_reward_values_dict['duration'], agent_reward_values_dict['duration']], axis=0)
# alert_final_values = np.mean([no_agent_reward_values_dict['alerts'], agent_reward_values_dict['alerts']], axis=0)
# alert_final_values_std = np.std([no_agent_reward_values_dict['alerts'], agent_reward_values_dict['alerts']], axis=0)
# with open("/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/splunk-v12/a2c_0.0_0.5_0.5__0.001/train/no_agent_reward_values_dict.json", "w") as f:
#     json.dump({"duration": duration_final_values.tolist(), "duration_std": duration_final_values_std.tolist(), "alerts": alert_final_values.tolist(), "alerts_std": alert_final_values_std.tolist()}, f)

# with open("/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/splunk-v12/ppo_0.0_0.5_0.5__0.001/train/no_agent_reward_values_dict.json", "w") as f:
#     json.dump({"duration": duration_final_values.tolist(), "duration_std": duration_final_values_std.tolist(), "alerts": alert_final_values.tolist(), "alerts_std": alert_final_values_std.tolist()}, f)

In [6]:
import plotly.graph_objects as go
import pandas as pd
import json
from pathlib import Path
import itertools

num_of_steps = 60
figures = {}

base_dir = Path("/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__")

def process_experiment(experiment_path, env_name, model_name, reward_parameter, learning_rate):
    try:
        with open(experiment_path / "train/reward_values_dict.json") as f:
            train_values = json.load(f)
        with open(experiment_path / "train/reward_dict.json") as f:
            train_values_reward = json.load(f)
        with open(experiment_path / "train/no_agent_reward_values_dict.json") as f:
            no_agent_train_values = json.load(f)
    except FileNotFoundError:
        return {}

    results = {}

    # Process rewards
    rewards_df = pd.DataFrame({
        'rewards': train_values_reward['total'],
        'step': range(len(train_values_reward['total']))
    })
    rewards_df['episode'] = rewards_df['step'] // num_of_steps + 1
    rewards_df = rewards_df.groupby('episode').agg({'rewards': 'sum'}).reset_index()
    rewards_df['mean_rewards'] = rewards_df['rewards'].rolling(window=num_of_steps).mean()

    results['rewards'] = rewards_df['rewards']
    results['mean_rewards'] = rewards_df['mean_rewards']
    results['episode'] = rewards_df['episode']

    # Process distributions
    if 'distributions' in train_values:
        distributions_df = pd.DataFrame({
            'distribution': train_values['distributions'],
            'step': range(len(train_values['distributions']))
        })
        distributions_df['episode'] = distributions_df['step'] // num_of_steps
        distributions_df['distribution'] = distributions_df['distribution'].rolling(window=num_of_steps).mean()
        distributions_df['mean_distribution'] = distributions_df['distribution'].groupby(distributions_df['episode']).transform('mean')

        results['distributions'] = distributions_df['distribution']
        results['mean_distributions'] = distributions_df['mean_distribution']
        results['distribution_step'] = distributions_df['step']
        results['distribution_episode'] = distributions_df['episode']

    # Process duration and alerts
    for key in ['duration', 'alerts']:
        if key in train_values and key in no_agent_train_values:
            max_length = max(len(train_values[key]), len(no_agent_train_values[key]))
            df = pd.DataFrame({
                'agent': train_values[key] + [None] * (max_length - len(train_values[key])),
                'no_agent': no_agent_train_values[key] + [None] * (max_length - len(no_agent_train_values[key])),
                'step': range(max_length)
            })
            df['difference'] = df['agent'] - df['no_agent']

            results[f'{key}_agent'] = df['agent']
            results[f'{key}_no_agent'] = df['no_agent']
            results[f'{key}_difference'] = df['difference']
            results[f'{key}_step'] = df['step']

    return results

def create_combined_charts(all_results, env_name):
    colors = itertools.cycle(['blue', 'orange', 'green', 'purple', 'orange', 'cyan', 'magenta', 'yellow'])

    # Rewards chart
    rewards_fig = go.Figure()
    mean_rewards_fig = go.Figure()
    for model, results in all_results.items():
        color = next(colors)
        rewards_fig.add_trace(go.Scatter(x=results['episode'], y=results['rewards'], mode='lines', name=model, line=dict(color=color)))
        mean_rewards_fig.add_trace(go.Scatter(x=results['episode'], y=results['mean_rewards'], mode='lines', name=model, line=dict(color=color)))

    rewards_fig.update_layout(title=f'{env_name}: Total Reward - All Models', xaxis_title='Episode', yaxis_title='Reward', width=1200)
    mean_rewards_fig.update_layout(title=f'{env_name}: Mean Reward - All Models', xaxis_title='Episode', yaxis_title='Mean Reward', width=1200)

    # Distributions chart
    if 'distributions' in next(iter(all_results.values())):
        distributions_fig = go.Figure()
        mean_distributions_fig = go.Figure()
        colors = itertools.cycle(['blue', 'orange', 'green', 'purple', 'orange', 'cyan', 'magenta', 'yellow'])
        for model, results in all_results.items():
            color = next(colors)
            distributions_fig.add_trace(go.Scatter(x=results['distribution_step'], y=results['distributions'], mode='lines', name=model, line=dict(color=color)))
            mean_distributions_fig.add_trace(go.Scatter(x=results['distribution_episode'], y=results['mean_distributions'], mode='lines', name=model, line=dict(color=color)))

        distributions_fig.update_layout(title=f'{env_name}: Distribution Values - All Models', xaxis_title='Step', yaxis_title='Distribution', width=1200)
        mean_distributions_fig.update_layout(title=f'{env_name}: Mean Distribution Values - All Models', xaxis_title='Episode', yaxis_title='Mean Distribution', width=1200)

    # Duration and Alerts charts
    duration_fig = go.Figure()
    duration_diff_fig = go.Figure()
    alerts_fig = go.Figure()
    alerts_diff_fig = go.Figure()
    colors = itertools.cycle(['blue', 'orange', 'green', 'purple', 'orange', 'cyan', 'magenta', 'yellow'])
    no_agent = True
    for model, results in all_results.items():
        color = next(colors)
        # Duration charts
        duration_fig.add_trace(go.Scatter(x=results['duration_step'], y=results['duration_agent'], mode='lines', name=f'{model} - Agent', line=dict(color=color)))
        if no_agent:
            duration_fig.add_trace(go.Scatter(x=results['duration_step'], y=results['duration_no_agent'], mode='lines', name=f'No Agent', line=dict(color="black", dash='dash')))
        duration_diff_fig.add_trace(go.Scatter(x=results['duration_step'], y=results['duration_difference'], mode='lines', name=model, line=dict(color=color)))

        # Alerts charts
        alerts_fig.add_trace(go.Scatter(x=results['alerts_step'], y=results['alerts_agent'], mode='lines', name=f'{model} - Agent', line=dict(color=color, dash='dash')))
        if no_agent:
            alerts_fig.add_trace(go.Scatter(x=results['alerts_step'], y=results['alerts_no_agent'], mode='lines', name=f'No Agent', line=dict(color='black', dash='dash')))
            no_agent = False
        alerts_diff_fig.add_trace(go.Scatter(x=results['alerts_step'], y=results['alerts_difference'], mode='lines', name=model, line=dict(color=color)))

    duration_fig.update_layout(title=f'{env_name}: Duration - All Models', xaxis_title='Step', yaxis_title='Duration', width=1200)
    duration_diff_fig.update_layout(title=f'{env_name}: Duration Difference (Agent - No Agent) - All Models', xaxis_title='Step', yaxis_title='Duration Difference', width=1200)
    alerts_fig.update_layout(title=f'{env_name}: Alerts - All Models', xaxis_title='Step', yaxis_title='Alerts', width=1200)
    alerts_diff_fig.update_layout(title=f'{env_name}: Alerts Difference (Agent - No Agent) - All Models', xaxis_title='Step', yaxis_title='Alerts Difference', width=1200)

    return [rewards_fig, mean_rewards_fig, distributions_fig, mean_distributions_fig, duration_fig, duration_diff_fig, alerts_fig, alerts_diff_fig]

# Main execution
for env_name in env_names:
    all_results = {}
    for model_name, learning_rate, reward_parameter in itertools.product(model_names, learning_rates, reward_parameters):
        for i in range (1,3):
            if reward_parameter == '0.0_0.3_0.7':
                continue
            experiment_path = base_dir / env_name / f"{model_name}_{reward_parameter}__{learning_rate}"/ f"Experiment_{i}"
            results = process_experiment(experiment_path, env_name, model_name, reward_parameter, learning_rate)
            if results:
                all_results[f"{model_name}_{reward_parameter}__{learning_rate}_Experiment{i}"] = results

    figures[env_name] = create_combined_charts(all_results, env_name)

# Display all figures
for env_name, env_figures in figures.items():
    for fig in env_figures:
        fig.show()

In [7]:
with open("/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/splunk-v12/ppo_0.0_0.1_0.9__0.001/train/reward_dict.json") as f:
    train_values = json.load(f)

In [8]:
len(train_values['distributions'])

300

In [9]:
from plotly import express as px
# total_rewards_df = pd.DataFrame({"reward":train_values['total']})
# total_rewards_df['step'] = range(len(train_values['total']))
# total_rewards_df['type'] = 'total'
duration_df = pd.DataFrame({"reward":train_values['duration']})
duration_df['step'] = range(len(train_values['duration']))
duration_df['type'] = 'duration'
alerts_df = pd.DataFrame({"reward":train_values['alerts'][1:]})
alerts_df['step'] = range(len(train_values['alerts'][1:]))
alerts_df['type'] = 'alerts'
distribution_df = pd.DataFrame({"reward":train_values['distributions']})
distribution_df['step'] = range(len(train_values['distributions']))
distribution_df['type'] = 'distribution'
df = pd.concat([duration_df,  distribution_df])
df

reward  step          type
0    0.863921     0      duration
1    0.661189     1      duration
2    0.596958     2      duration
3    0.616130     3      duration
4    0.575553     4      duration
..        ...   ...           ...
295  0.617032   295  distribution
296  0.754970   296  distribution
297  0.670666   297  distribution
298  0.931023   298  distribution
299  0.721019   299  distribution

[600 rows x 3 columns]

In [10]:
px.histogram(df, x="reward", color="type", title="A2C 0.0_0.1_0.9__0.001", width=1200).show()

In [11]:
def dict_to_df(values_dict):
    energy_df = pd.DataFrame([values_dict['energy'],values_dict['duration'],values_dict['num_of_rules']]).T
    energy_df.columns = ['energy','duration','num_of_rules']
    energy_df = energy_df.reset_index()
    return energy_df

In [12]:
def dict_to_df_distribution(values_dict):
    distiribution_df = pd.DataFrame(values_dict['distributions'])
    return distiribution_df

In [13]:
def dict_to_df_alert(values_dict):
    alert_df = pd.DataFrame(values_dict['alerts'])
    return alert_df

In [14]:
import os
import json
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def load_and_process(file_path, method_name, env_name, experiment_num):
    with open(f"{file_path}reward_values_dict.json", 'r') as file:
        print(file_path)
        data = json.load(file)
    energy_df = dict_to_df(data)
    energy_df['method'] = f"{method_name}_experiment_{experiment_num}"
    energy_df['env'] = env_name
    distribution_df = dict_to_df_distribution(data)
    distribution_df['method'] = f"{method_name}_experiment_{experiment_num}"
    distribution_df['env'] = env_name
    alert_df = dict_to_df_alert(data)
    alert_df['method'] = f"{method_name}_experiment_{experiment_num}"
    alert_df['env'] = env_name
    duration_df = pd.DataFrame(data['duration'], columns=['duration'])
    duration_df['method'] = f"{method_name}_experiment_{experiment_num}"
    duration_df['env'] = env_name

    return energy_df, distribution_df, alert_df, duration_df

def process_environments(env_names, num_of_episodes):
    dfs = []
    distribution_dfs = []
    alerts_dfs = []
    duration_dfs = []

    for env_name in env_names:
        experiment_dir = f"/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/{env_name}"

        for model_name in model_names:
            for learning_rate in learning_rates:
                for reward_parameter in reward_parameters:
                    for i in range(1,4):
                        # if reward_parameter != '0.0_0.5_0.5':
                        #     continue
                        file_path = os.path.join(experiment_dir, f"{model_name}_{reward_parameter}__{learning_rate}/Experiment_{i}/test_{num_of_episodes}/")
                        if os.path.exists(file_path):
                            method_name = f"{model_name}_{reward_parameter}_{learning_rate}"
                            energy_df, distribution_df, alert_df, duration_df = load_and_process(file_path, method_name, env_name, i)
                            dfs.append(energy_df)
                            distribution_dfs.append(distribution_df)
                            alerts_dfs.append(alert_df)
                            duration_dfs.append(duration_df)
        fake_start_date = "05/21/2024:13:00:00"  #"05/04/2024:21:00:00"#
        # Process passive test
        passive_test_path = os.path.join(experiment_dir, f"no_agent_{num_of_episodes}_{fake_start_date}/")
        if os.path.exists(passive_test_path):
            passive_energy_df, passive_distribution_df, passive_alert_df, passive_duration_df = load_and_process(passive_test_path, 'test_no_agent', env_name, 0)
            dfs.append(passive_energy_df)
            distribution_dfs.append(passive_distribution_df)
            alerts_dfs.append(passive_alert_df)
            duration_dfs.append(passive_duration_df)

        # Process random agent test
        random_agent_path = os.path.join(experiment_dir, f"baseline_random_{num_of_episodes}_{fake_start_date}/")
        if os.path.exists(random_agent_path):
            random_energy_df, random_distribution_df, random_alert_df, random_duration_df = load_and_process(random_agent_path, 'test_random_agent', env_name, 0)
            dfs.append(random_energy_df)
            distribution_dfs.append(random_distribution_df)
            alerts_dfs.append(random_alert_df)
            duration_dfs.append(random_duration_df)

    # Concatenate all DataFrames
    energy_df = pd.concat(dfs).reset_index(drop=True)
    distribution_df = pd.concat(distribution_dfs, axis=0).reset_index(drop=False)
    distribution_df.rename(columns={0:"distribution"}, inplace=True)
    alert_df = pd.concat(alerts_dfs, axis=0).reset_index(drop=False)
    alert_df.rename(columns={0: 'alerts'}, inplace=True)
    duration_df = pd.concat(duration_dfs, axis=0).reset_index(drop=False)

    return energy_df, distribution_df, alert_df, duration_df

def create_plot(alert_df, duration_df, distribution_df, env_names, num_of_episodes):
    print("Alert DataFrame columns:", alert_df.columns)
    print("Duration DataFrame columns:", duration_df.columns)
    print("Distribution DataFrame columns:", distribution_df.columns)

    # Calculate means
    alert_mean = alert_df.groupby(['method', 'env'])['alerts'].mean().reset_index()
    duration_mean = duration_df.groupby(['method', 'env'])['duration'].mean().reset_index()
    distribution_mean = distribution_df.groupby(['method', 'env'])['distribution'].mean().reset_index()

    # Create merged plot for alerts, durations, and distributions
    fig = make_subplots(rows=3, cols=1, subplot_titles=('Mean Alerts', 'Mean Durations', 'Mean Distributions'),
                        shared_xaxes=True)

    env_patterns = ['+', '/', 'x', '-', '|', '+', '.']

    for i, env in enumerate(env_names):
        fig.add_trace(go.Bar(x=alert_mean[alert_mean['env'] == env]['method'], 
                             y=alert_mean[alert_mean['env'] == env]['alerts'], 
                             name=f'Alerts - {env}', 
                             marker_pattern_shape=env_patterns[i % len(env_patterns)]), row=1, col=1)
        
        fig.add_trace(go.Bar(x=duration_mean[duration_mean['env'] == env]['method'], 
                             y=duration_mean[duration_mean['env'] == env]['duration'], 
                             name=f'Durations - {env}', 
                             marker_pattern_shape=env_patterns[i % len(env_patterns)]), row=2, col=1)
        
        fig.add_trace(go.Bar(x=distribution_mean[distribution_mean['env'] == env]['method'], 
                             y=distribution_mean[distribution_mean['env'] == env]['distribution'], 
                             name=f'Distributions - {env}', 
                             marker_pattern_shape=env_patterns[i % len(env_patterns)]), row=3, col=1)

    # Update layout
    fig.update_layout(height=1000, width=800, 
                      title_text=f"Mean Alerts, Durations, and Distributions by Method and Environment ({num_of_episodes} episodes)",
                      barmode='group')
    fig.update_xaxes(tickangle=-45, title_text="Method")
    fig.update_yaxes(title_text="Mean Count", col=1)
    fig.update_yaxes(title_text="Mean Duration", col=2)
    fig.update_yaxes(title_text="Mean Distribution", col=3)

    # Show the figure
    fig.show()
num_of_episodes_ = [60, 30]
# Main execution
for num_of_episodes in num_of_episodes_:
    try:
        # Process all environments except the last one
        energy_df, distribution_df, alert_df, duration_df = process_environments(env_names[:-1], num_of_episodes)
        create_plot(alert_df, duration_df, distribution_df, env_names[:-1], num_of_episodes)
    except Exception as e:
        print('error ', e)
        
    try:
        # Process the last environment separately
        last_env = env_names[-1]
        energy_df, distribution_df, alert_df, duration_df = process_environments([last_env], num_of_episodes)
        create_plot(alert_df, duration_df, distribution_df, [last_env], num_of_episodes)
    except Exception as e:
        print('error ', e)
        

error  No objects to concatenate
/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/splunk-v13/mlp_ppo_0.0_0.5_0.5__0.001/Experiment_1/test_60/
/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/splunk-v13/mlp_ppo_0.0_0.5_0.5__0.001/Experiment_3/test_60/
/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/splunk-v13/no_agent_60_05/21/2024:13:00:00/
/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/splunk-v13/baseline_random_60_05/21/2024:13:00:00/
Alert DataFrame columns: Index(['index', 'alerts', 'method', 'env'], dtype='object')
Duration DataFrame columns: Index(['index', 'duration', 'method', 'env'], dtype='object')
Distribution DataFrame columns: Index(['index', 'distribution', 'method', 'env'], dtype='object')


error  No objects to concatenate
/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/experiments__/splunk-v13/mlp_ppo_0.0_0.5_0.5__0.001/Experiment_2/test_30/
Alert DataFrame columns: Index(['index', 'alerts', 'method', 'env'], dtype='object')
Duration DataFrame columns: Index(['index', 'duration', 'method', 'env'], dtype='object')
Distribution DataFrame columns: Index(['index', 'distribution', 'method', 'env'], dtype='object')


In [18]:
color_map = alt.Scale(domain=['test_random_agent', 'a2c_0.3_0.3_0.4_0.001', 'test_no_agent'], range=['black','red',  'blue'])
alt.Chart(alert_df).mark_bar().encode(
    x='method',
    y='mean(alerts)',
    color=alt.Color('method', scale=alt.Scale(scheme='category20')),

    # color={'field': 'method', 'type': 'nominal', 'scale': {'scheme': 'category20'}},
    tooltip=['method', 'alerts']
).properties(
    title='Alerts',
)

alt.Chart(...)

In [19]:
# alert_df = alert_df[alert_df['step'] < 20]
color_map = alt.Scale(domain=['test_random_agent', 'a2c_0.3_0.3_0.4_0.001', 'test_no_agent'], range=['black','red',  'blue'])
alt.Chart(alert_df).mark_line().encode(
# alt.Chart(alert_df[alert_df['method'].isin(['test_random_agent', 'a2c_0.5_0.1_0.4_0.001', 'a2c_0.5_0.1_0.4_0.005'])]).mark_line().encode(
    x='index',
    y='mean(alerts)',
    color={'field': 'method', 'type': 'nominal',"sort":"-color"},
    
).properties(
    title='alerts',
    width=1200,
)

alt.Chart(...)

In [19]:
# max_actions_value = 20000
# baseline_dfs_list = []
# action_values = [0, max_actions_value, max_actions_value//2]
# for search_window in [5, 15, 30, 60]:
#         for max_actions_value in [0,1000, 20000, 50000, 200000]:#, 100000, 200000]:
#             i = f"{search_window}_{max_actions_value}"
#             with open(f'{expirment_dir}/test_baseline_{i}/reward_values_dict.json') as f:
#                 baseline_values = json.load(f)
#             energy_df_baseline = dict_to_df(baseline_values)
#             energy_df_baseline['method'] = f'baseline_{i}'
#             baseline_dfs_list.append(energy_df_baseline)
# energy_df = pd.concat(baseline_dfs_list).reset_index()
# energy_df.rename(columns={'level_0': 'episode'}, inplace=True)

        



In [20]:
# energy_df = energy_df[energy_df['method'] == 'baseline02'].reset_index()
# for i in range(18):
#     if i < 6:
#         j = 0
#     elif i < 12:
#         j = 1
#     else:
#         j = 2
#     energy_df.loc[i, 'method'] = f'baseline0{j}'
# energy_df

In [21]:
num_of_rules = 7

In [22]:
# energy_df[energy_df['num_of_rules']!=num_of_rules]['episode'].unique()

In [23]:
# energy_df.drop(energy_df[energy_df['episode'].isin(energy_df[energy_df['num_of_rules']!=num_of_rules]['episode'].unique())].index, inplace=True)
# energy_df

In [24]:
distribution_df

index  distribution                     method         env
0         0      0.312287  mlp_ppo_0.0_0.5_0.5_0.001  splunk-v13
1         1      0.286693  mlp_ppo_0.0_0.5_0.5_0.001  splunk-v13
2         2      0.209726  mlp_ppo_0.0_0.5_0.5_0.001  splunk-v13
3         3      0.230953  mlp_ppo_0.0_0.5_0.5_0.001  splunk-v13
4         4      0.241017  mlp_ppo_0.0_0.5_0.5_0.001  splunk-v13
...     ...           ...                        ...         ...
7255   3595      0.269010          test_random_agent  splunk-v13
7256   3596      0.270638          test_random_agent  splunk-v13
7257   3597      0.271198          test_random_agent  splunk-v13
7258   3598      0.271544          test_random_agent  splunk-v13
7259   3599      0.272111          test_random_agent  splunk-v13

[7260 rows x 4 columns]

In [25]:
num_of_steps = 60

In [26]:
distribution_df = add_episode_column(distribution_df, num_of_steps)


In [27]:
distribution_df = distribution_df

In [28]:
# distribution_df = distribution_df[distribution_df['episode'] < 20]
# alt.Chart(distribution_df).mark_line().encode(
#     x='step',
#     y='distribution',
#     color=alt.Color('method', scale=alt.Scale(scheme='cividis'), sort='-y'),

# ).properties(
#     title='Distributions',
#     width=1200,
# )
import plotly.express as px

px.line(distribution_df, x='index', y='distribution', color='method', title='Distributions', color_discrete_sequence=px.colors.sequential.Agsunset)


In [29]:

alt.Chart(distribution_df.groupby(['episode','method']).mean().reset_index().groupby('method').mean().reset_index()   ).mark_bar().encode(
    x=alt.X('method', sort='-x'),
    y=alt.Y('distribution'),
    color=alt.Color('method', scale=alt.Scale(scheme='category20')),
    tooltip=['method','distribution'],
    # text=alt.Text('mean', format='.2f')
).properties(
    title='Distributions per method',

)

TypeError: Could not convert splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13splunk-v13 to numeric

In [ ]:
# energy_df = energy_df.drop(energy_df[energy_df['episode'] >=20].index)

In [ ]:
alert_df[['model','alpha','beta','gamma','learning_rate']] = alert_df['method'].str.split('_', expand=True)


In [30]:
alert_df.groupby(['model']).mean(numeric_only=True).reset_index()


KeyError: 'model'

In [31]:
alert_df.groupby(['alpha','beta','gamma']).mean(numeric_only=True).reset_index()


KeyError: 'alpha'

In [32]:
alert_df.groupby(['learning_rate']).mean(numeric_only=True).reset_index()


KeyError: 'learning_rate'

In [33]:
distribution_df[['model','alpha','beta','gamma','learning_rate']] = distribution_df['method'].str.split('_', expand=True)

ValueError: Columns must be same length as key

In [ ]:
distribution_df.groupby(['model']).mean(numeric_only=True).reset_index()


model        index  distribution     episode
0   a2c  1795.403425  7.116981e-03  238.950094
1   ppo  1799.500000  1.300377e-01  658.400000
2  test    59.500000  1.000000e-12  840.400000

In [34]:
distribution_df.groupby(['alpha','beta','gamma']).mean(numeric_only=True).reset_index()


KeyError: 'alpha'

In [35]:
distribution_df.groupby(['learning_rate']).mean(numeric_only=True).reset_index()


KeyError: 'learning_rate'

In [36]:
energy_df[['model','alpha','beta','gamma','learning_rate']] = energy_df['method'].str.split('_', expand=True)


ValueError: Columns must be same length as key

In [37]:
energy_df.groupby(['model']).mean(numeric_only=True).reset_index()

KeyError: 'model'

In [38]:
energy_df.groupby(['alpha','beta','gamma']).mean(numeric_only=True).reset_index()

KeyError: 'alpha'

In [39]:
energy_df.groupby(['learning_rate']).mean(numeric_only=True).reset_index()

KeyError: 'learning_rate'

In [40]:
# make a bar chart of the mean duration with std
color_map = alt.Scale(domain=['test_no_agent', 'a2c_0.3_0.3_0.4_0.001'], range=['red', 'blue'])
alt.Chart(energy_df.groupby('method').describe()['duration'].reset_index()).mark_bar().encode(
# alt.Chart(energy_df.groupby('method').describe()['duration'].reset_index()).mark_bar().encode(
    x=alt.X('method', sort='-x'),
    y=alt.Y('mean'),
    color=alt.Color('method', scale=alt.Scale(scheme='category20')),
    # color=alt.Color('method', scale=alt.Scale(scheme='category20')),
    tooltip=['method', 'mean', 'std'],
    text=alt.Text('mean', format='.2f')
).properties(
    title='Duration per method',

)


alt.Chart(...)

In [41]:
energy_df.describe()

index  energy    duration  num_of_rules
count  180.000000     0.0  180.000000           0.0
mean    29.500000     NaN   16.760906           NaN
std     17.366409     NaN    1.294651           NaN
min      0.000000     NaN   13.647746           NaN
25%     14.750000     NaN   16.100282           NaN
50%     29.500000     NaN   16.563327           NaN
75%     44.250000     NaN   17.131821           NaN
max     59.000000     NaN   26.567327           NaN

In [43]:
# make a bar chart of the mean duration with std
alt.Chart(energy_df.groupby('method').describe()['energy'].reset_index()).mark_bar().encode(
    x=alt.X('method', sort='-y'),
    y=alt.Y('mean', sort='-x'),
    color='method',
    tooltip=['method', 'mean', 'std'],
    text=alt.Text('mean', format='.2f')
).properties(
    title='Energy per method',

)

alt.Chart(...)

In [44]:
alert_df.rename(columns={'step': 'episode'}, inplace=True)

In [45]:
energy_df

index  energy   duration  num_of_rules                 method  \
0        0     NaN  19.135439           NaN  a2c_0.0_0.1_0.9_0.001   
1        1     NaN  18.424049           NaN  a2c_0.0_0.1_0.9_0.001   
2        2     NaN  18.929030           NaN  a2c_0.0_0.1_0.9_0.001   
3        3     NaN  18.945974           NaN  a2c_0.0_0.1_0.9_0.001   
4        4     NaN  19.670390           NaN  a2c_0.0_0.1_0.9_0.001   
..     ...     ...        ...           ...                    ...   
955    115     NaN  17.296996           NaN          test_no_agent   
956    116     NaN  18.310334           NaN          test_no_agent   
957    117     NaN  18.164222           NaN          test_no_agent   
958    118     NaN  17.983409           NaN          test_no_agent   
959    119     NaN  19.047912           NaN          test_no_agent   

            env model alpha   beta gamma learning_rate  
0    splunk-v12   a2c   0.0    0.1   0.9         0.001  
1    splunk-v12   a2c   0.0    0.1   0.9         0.001  
2    splunk-v12   a2c   0.0    0.1   0.9         0.001  
3    splunk-v12   a2c   0.0    0.1   0.9         0.001  
4    splunk-v12   a2c   0.0    0.1   0.9         0.001  
..          ...   ...   ...    ...   ...           ...  
955  splunk-v12  test    no  agent  None          None  
956  splunk-v12  test    no  agent  None          None  
957  splunk-v12  test    no  agent  None          None  
958  splunk-v12  test    no  agent  None          None  
959  splunk-v12  test    no  agent  None          None  

[960 rows x 11 columns]

In [46]:
energy_df.drop(columns=['model','alpha','beta','gamma','learning_rate'], inplace=True)

In [47]:
energy_df

index  energy   duration  num_of_rules                 method         env
0        0     NaN  19.135439           NaN  a2c_0.0_0.1_0.9_0.001  splunk-v12
1        1     NaN  18.424049           NaN  a2c_0.0_0.1_0.9_0.001  splunk-v12
2        2     NaN  18.929030           NaN  a2c_0.0_0.1_0.9_0.001  splunk-v12
3        3     NaN  18.945974           NaN  a2c_0.0_0.1_0.9_0.001  splunk-v12
4        4     NaN  19.670390           NaN  a2c_0.0_0.1_0.9_0.001  splunk-v12
..     ...     ...        ...           ...                    ...         ...
955    115     NaN  17.296996           NaN          test_no_agent  splunk-v12
956    116     NaN  18.310334           NaN          test_no_agent  splunk-v12
957    117     NaN  18.164222           NaN          test_no_agent  splunk-v12
958    118     NaN  17.983409           NaN          test_no_agent  splunk-v12
959    119     NaN  19.047912           NaN          test_no_agent  splunk-v12

[960 rows x 6 columns]

In [43]:
# color_map = alt.Scale(domain=['DRL', 'test_no_agent', 'test_random_agent'], range=['red', 'green', 'blue'])
# color_map = alt.Scale(domain=['test_no_agent', 'a2c_0.5_0.1_0.4_0.001'], range=['red', 'blue'])
# # color_map = alt.Scale(domain=['test_no_agent', 'a2c_0.5_0.1_0.4_0.001', 'a2c_0.5_0.1_0.4_0.005'], range=['red', 'blue', 'green'])
# alt.Chart(energy_df).mark_line(point=False).encode(
# # alt.Chart(energy_df[energy_df['method'].isin(['test_no_agent', 'a2c_0.5_0.1_0.4_0.001', 'a2c_0.5_0.1_0.4_0.005'])]).mark_line(point=False).encode(
#     x='episode',
#     y='duration',
#     color={'field': 'method', 'type': 'nominal',"sort":"-color"},
    
    
# ).properties(
#     title='Duration of the DRL methods vs the random methods',
#     width=1200,
# )
import plotly.express as px

px.line(energy_df.groupby(['method','index', 'env']).mean().reset_index(), x='index', y='duration', color='method', title='Duration of the DRL methods vs the random methods', color_discrete_sequence=px.colors.qualitative.Set1)


In [49]:
energy_df

index  energy   duration  num_of_rules                 method         env
0        0     NaN  19.135439           NaN  a2c_0.0_0.1_0.9_0.001  splunk-v12
1        1     NaN  18.424049           NaN  a2c_0.0_0.1_0.9_0.001  splunk-v12
2        2     NaN  18.929030           NaN  a2c_0.0_0.1_0.9_0.001  splunk-v12
3        3     NaN  18.945974           NaN  a2c_0.0_0.1_0.9_0.001  splunk-v12
4        4     NaN  19.670390           NaN  a2c_0.0_0.1_0.9_0.001  splunk-v12
..     ...     ...        ...           ...                    ...         ...
955    115     NaN  17.296996           NaN          test_no_agent  splunk-v12
956    116     NaN  18.310334           NaN          test_no_agent  splunk-v12
957    117     NaN  18.164222           NaN          test_no_agent  splunk-v12
958    118     NaN  17.983409           NaN          test_no_agent  splunk-v12
959    119     NaN  19.047912           NaN          test_no_agent  splunk-v12

[960 rows x 6 columns]

In [50]:
distribution_df

index  distribution                 method         env  episode model  \
0          0  1.043702e-02  a2c_0.0_0.1_0.9_0.001  splunk-v12        0   a2c   
1          1  7.610776e-03  a2c_0.0_0.1_0.9_0.001  splunk-v12        0   a2c   
2          2  6.259001e-03  a2c_0.0_0.1_0.9_0.001  splunk-v12        0   a2c   
3          3  6.075454e-03  a2c_0.0_0.1_0.9_0.001  splunk-v12        0   a2c   
4          4  1.439270e-02  a2c_0.0_0.1_0.9_0.001  splunk-v12        0   a2c   
...      ...           ...                    ...         ...      ...   ...   
25282    115  1.000000e-12          test_no_agent  splunk-v12      842  test   
25283    116  1.000000e-12          test_no_agent  splunk-v12      842  test   
25284    117  1.000000e-12          test_no_agent  splunk-v12      842  test   
25285    118  1.000000e-12          test_no_agent  splunk-v12      842  test   
25286    119  1.000000e-12          test_no_agent  splunk-v12      842  test   

      alpha   beta gamma learning_rate  
0       0.0    0.1   0.9         0.001  
1       0.0    0.1   0.9         0.001  
2       0.0    0.1   0.9         0.001  
3       0.0    0.1   0.9         0.001  
4       0.0    0.1   0.9         0.001  
...     ...    ...   ...           ...  
25282    no  agent  None          None  
25283    no  agent  None          None  
25284    no  agent  None          None  
25285    no  agent  None          None  
25286    no  agent  None          None  

[25287 rows x 10 columns]

In [53]:
# merge all the results dataframes
distribution_df = distribution_df.groupby(['episode','method']).mean().reset_index().groupby('method').mean().reset_index()   
alert_df = alert_df[alert_df['episode'] < 20]
alert_df = alert_df.groupby(['episode','method']).mean().reset_index().groupby('method').mean().reset_index()
energy_df = energy_df[energy_df['episode'] < 20]
energy_df = energy_df.groupby('method').mean().reset_index()


TypeError: Could not convert splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12splunk-v12 to numeric

In [54]:
merged_df = pd.merge(energy_df, alert_df, on=['method'])
merged_df = pd.merge(merged_df, distribution_df, on=['method'])
merged_df[['method', 'duration', 'alerts', 'distribution']]

In [ ]:
alt.Chart(energy_df).mark_line(point=True).encode(
    x='episode',
    y='energy',
    color='method'
    
).properties(
    title='Energy consumption of the DRL method vs the baseline methods',
    width=800,
)

ValueError: Unable to determine data type for the field "episode"; verify that the field name is not misspelled. If you are referencing a field from a transform, also confirm that the data type is specified correctly.

alt.Chart(...)

In [ ]:
from splunk_tools import SplunkTools
savedsearches = ["Windows Event For Service Disabled",
                 "Detect New Local Admin account",
                 "ESCU Network Share Discovery Via Dir Command Rule",
                 "Known Services Killed by Ransomware",
                 "Non Chrome Process Accessing Chrome Default Dir",
                 "Kerberoasting spn request with RC4 encryption",
                 "Clop Ransomware Known Service Name"]
splunk_tools = SplunkTools(savedsearches)
rules_names = splunk_tools.active_saved_searches

In [ ]:

num_of_episodes = 120
def get_time_rule_energy_df(mode, file_name):
    with open(f'{experiment_dir}/{mode}/{file_name}.json') as f:
        time_rules_energy_dict_test = json.load(f)
    time_rules_energy_dict_test_data = []
    
    for e in time_rules_energy_dict_test:
        # if len(v) == 0:
        #     for n in rules_names:
        #         time_rules_energy_dict_test_data.append({'time': e['time_range'], 'rule_name': n, 'energy': 0})
        # rules_names = []
        
        for i, r in enumerate(e['rules']):
            rule_name = rules_names[i]['title']
            time_rules_energy_dict_test_data.append({'time': e['time_range'], 'rule_name': rule_name, 'duration': r, 'num_of_rules': len(e['rules']), 'method': mode})
    return pd.DataFrame(time_rules_energy_dict_test_data)
dfs = []
for model_name in model_names:
    for learning_rate in learning_rates:
        for reward_parameter in reward_parameters:
            try:
                time_rules_energy_df = get_time_rule_energy_df(f"{model_name}_{reward_parameter}__{learning_rate}/test_{num_of_episodes}", 'time_rules_energy')
            except:
                continue
            dfs.append(time_rules_energy_df)       
random_baseline_time_rules_energy_df = get_time_rule_energy_df(f"baseline_random_{num_of_episodes}", 'time_rules_energy')
dfs.append(random_baseline_time_rules_energy_df)
passive_baseline_time_rules_energy_df = get_time_rule_energy_df(f"no_agent_{num_of_episodes}", 'time_rules_energy')
dfs.append(passive_baseline_time_rules_energy_df)
# autopic_baseline_time_rules_energy_df = get_time_rule_energy_df("baseline_autopic", 'time_rules_energy')
# dfs.append(autopic_baseline_time_rules_energy_df)
time_rules_energy_df = pd.concat(dfs).reset_index()
time_rules_energy_df


In [ ]:
# concat the dataframes into one dataframe with one column for the energy and one column for the method
# test['method'] = 'DRL'
# baseline1['method'] = 'baseline'
# baseline2['method'] = 'baseline2'
# time_rules_energy_df = pd.concat([test,baseline1, baseline2])
time_to_index = {time:i for (i, time) in enumerate(time_rules_energy_df['time'].unique())}
time_rules_energy_df['index'] = time_rules_energy_df['time'].apply(lambda x: time_to_index[x])

In [ ]:
relevant_logtypes = sorted(list({f"{logtype[0]}_{logtype[1]}"  for rule in time_rules_energy_df['rule_name'].unique() for logtype  in section_logtypes[rule]})) #[(x[0], str(x[1])) for x in state_span]
def get_time_action_df(mode, file_name):
    with open(f'{experiment_dir}/{mode}/{file_name}.json') as f:
        time_rules_energy_dict_test = json.load(f)
        print(time_rules_energy_dict_test)
    df = pd.DataFrame(time_rules_energy_dict_test)#, columns=relevant_logtypes+['wineventlog:security_4624'])
    df['method'] = mode
    return df
dfs = []
for model_name in model_names:
    for learning_rate in learning_rates:
        for reward_parameter in reward_parameters:
            try:
                action_df_test = get_time_action_df(f"{model_name}_{reward_parameter}__{learning_rate}/test_{num_of_episodes}", 'action_dict')
            except:
                continue
            dfs.append(action_df_test)
random_baseline_action_df = get_time_action_df(f"baseline_random_{num_of_episodes}", 'action_dict')
dfs.append(random_baseline_action_df)
passive_action_df = get_time_action_df(f"no_agent_{num_of_episodes}", 'action_dict')
dfs.append(passive_action_df)
# autopic_action_df = get_time_action_df("baseline_autopic", 'action_dict')
# dfs.append(autopic_action_df)
time_action_df = pd.concat(dfs).reset_index()
time_action_df

In [ ]:
time_action_df.columns 

In [ ]:
time_action_df.columns = ['index']+[logtype+f"__{i}" for logtype in relevant_logtypes for i in range(2)] + ['wineventlog:security_4624__0']+['method']
time_action_df

In [ ]:
time_action_df = time_action_df.melt(id_vars=['index', 'method'], var_name='logtype', value_name='amount')
time_action_df

In [ ]:
time_action_df[['logtype', 'is_trigger']] = time_action_df['logtype'].str.split('__', expand=True)

In [ ]:
time_action_df['logtype']

In [ ]:
# concat the dataframes into one dataframe with one column for the energy and one column for the method
# test_action['method'] = 'DRL'
# baseline1_action['method'] = 'baseline'
# baseline2_action['method'] = 'baseline2'
# time_action_df = pd.concat([test_action,baseline1_action])
# time_action_df = pd.concat(baselines)

# time_action_df['time'] = time_action_df['time'].apply(lambda x: '_'.join(x))

# create a chart that shows the energy consumption of each rule for each method at each time
alt.Chart(time_action_df).mark_bar().encode(
    x=alt.X('logtype', axis=alt.Axis(labelLimit=1000)),
    y='amount:Q',
    column="index",
    color='method',
    row='is_trigger',
).properties(
    title='Action of the DRL method vs the baseline methods',
    
    
)

In [ ]:
logtypes_by_rule_dict = {'Detect Network Connections to Non-Standard Ports':["XmlWinEventLog:Microsoft-Windows-Sysmon/Operational_3"],
 'Disabled Security Tool': ["XmlWinEventLog:Microsoft-Windows-Sysmon/Operational_16"],
 'Monitor for Logon Failures': ["wineventlog:security_4625"],
 'Monitor for Whitelisting bypass attempts': ["wineventlog:security_4688"],
 'System or Application Error': ["wineventlog:system_1074","wineventlog:system_6008", "wineventlog:application_1000"],
 'Creation of a New Local User Account': ["wineventlog:security_4720"],
 'Monitor for Suspicious_Administrative Processes': ["wineventlog:security_4688"],
 'Monitor for Suspicious Network IP’s': ["wineventlog:security_4663"],
 'Monitor for Service State Changes': ["wineventlog:system_7040"],
 'Suspicious Remote Thread Creation': ["XmlWinEventLog:Microsoft-Windows-Sysmon/Operational_8"],
 'Monitor for Logon Success': ["wineventlog:security_4624"],
 'Monitor for File Shares': ["wineventlog:security_5140"],
 'Monitor for Changes to Firewall Rules': ["wineventlog:security_2005"],
 'User Added to Privileged Group': ["wineventlog:security_4728","wineventlog:security_4732","wineventlog:security_4756"],
 'Monitor for Additions to Firewall Rules': ["wineventlog:security_2004"],
 'Detected Registry Modification': ["XmlWinEventLog:Microsoft-Windows-Sysmon/Operational_12","XmlWinEventLog:Microsoft-Windows-Sysmon/Operational_13","XmlWinEventLog:Microsoft-Windows-Sysmon/Operational_14"],
 'An Account Was Logged off': ["wineventlog:security_4634"] ,
 'Detect Network Connections from Non-Browser or Non-Email Client': ["XmlWinEventLog:Microsoft-Windows-Sysmon/Operational_3"],
 'Modification of Executable File': ["XmlWinEventLog:Microsoft-Windows-Sysmon/Operational_11"],
 'Monitor for Administrative and Guest Logon Failures': ["wineventlog:security_4625"],
 'Monitor for New Service Installs': ["wineventlog:security_7045"],
 'Monitor for Registry Changes': ["wineventlog:security_4657"],
 'Multiple Failed Logins from the Same Source': ["wineventlog:security_4625"],
 'Multiple Network Connections to Same Port on External Hosts': ["XmlWinEventLog:Microsoft-Windows-Sysmon/Operational_3"],
 'New Local Admin Account': ["wineventlog:security_4720", "wineventlog:security_4732"],
 'ESCU Network Share Discovery Via Dir Command Rule': ['wineventlog:security_5140'],
 'ESCU Windows Rapid Authentication On Multiple Hosts Rule': ['wineventlog:security_4624'],
 'Detect New Local Admin account':[('wineventlog:security_4732')],
"Known Services Killed by Ransomware": [('wineventlog:system_7036')],
"Non Chrome Process Accessing Chrome Default Dir":[('wineventlog:security_4663')],
 'Windows Event For Service Disabled': [('wineventlog:system_7040')],
 'Process Opened a Network Connection': ["XmlWinEventLog:Microsoft-Windows-Sysmon/Operational_3"],
 'User Login with Local Credentials': ["wineventlog:security_4624"],
 'Windows Event Log Clearing Events': ["wineventlog:security_1102", "wineventlog:system_104", "wineventlog:security_1100"],
 "Kerberoasting spn request with RC4 encryption": [('wineventlog:security_4769')],
 "Clop Ransomware Known Service Name": [('wineventlog:system_7045')],
 }
logtypes_by_rule_dict = {rule.lower(): [logtype.lower() for logtype in logtypes] for rule, logtypes in logtypes_by_rule_dict.items()}
# logtypes_by_rule_dict

In [ ]:
time_action_df

In [ ]:
time_rules_energy_df['action_amount'] = 0
time_rules_energy_df['is_trigger'] = 0 
time_action_df['logtype'] = time_action_df['logtype'].apply(lambda x: x.strip('[').strip(']').strip('(').strip(')').split(',')).apply(lambda x: '_'.join(x).replace("\'", '').replace(" ", ''))
for method in time_rules_energy_df['method'].unique():
    for i, time in enumerate(time_rules_energy_df['time'].unique()):
        for rule in time_rules_energy_df['rule_name'].unique():
            relevant_log_types = logtypes_by_rule_dict[rule.lower()]
            # relevant_log_types = [str(logtype.split('_')) for logtype in relevant_log_types]
            print(relevant_log_types)
            print(time, method, rule)
            for is_trigger in ['0', '1']:

                amount = time_action_df[(time_action_df['index'] == i) & (time_action_df['method'] == method)&(time_action_df['is_trigger'] == is_trigger) & (time_action_df['logtype'].isin(relevant_log_types)) ]['amount'].sum()
                print('amount', amount)
                # print( time_rules_energy_df[(time_rules_energy_df['time'] == time) & (time_rules_energy_df['method'] == method) & (time_rules_energy_df['rule_name'] == rule)])
                if is_trigger == '0':
                    is_trigger = 'no_trigger'
                else:
                    is_trigger = 'trigger'
                time_rules_energy_df.loc[(time_rules_energy_df['time'] == f"{time}") & (time_rules_energy_df['method'] == method) & (time_rules_energy_df['rule_name'] == rule), f'{is_trigger}_action_amount'] = amount
                

In [ ]:
time_rules_energy_df

In [ ]:
x = time_rules_energy_df.melt(id_vars=['time', 'rule_name', 'method', 'duration'], value_vars=['no_trigger_action_amount', 'trigger_action_amount'], var_name='action_type', value_name='act_amount')

In [ ]:
x[(x['method']=="ppo")&(x["action_type"]=="no_trigger_action_amount")]

In [ ]:
x.groupby(['method', 'time']).sum()

In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

# Assuming x is your DataFrame
# Example data:
# x = ...
linestyle_dict = {'no_trigger_action_amount': '-', 'trigger_action_amount': '--'}
# Sort the DataFrame by 'time'
x = x.sort_values(by=['method', 'rule_name', 'time'])

# Create separate subplots for each facet
fig, axes = plt.subplots(nrows=x['rule_name'].nunique(), ncols=x['method'].nunique(), figsize=(60, 30), sharex=True, sharey='col')

# Flatten the axes array for easy indexing
axes = axes.flatten()

# Calculate global max and min values for 'act_amount' and 'duration'
global_max_amount = x['act_amount'].max()
global_min_amount = x['act_amount'].min()
global_max_duration = x['duration'].max()
global_min_duration = x['duration'].min()

# Iterate over facets and plot on each subplot
for i, rule_name in enumerate(x['rule_name'].unique()):
    for j, method in enumerate(x['method'].unique()):
        subset = x[(x['method'] == method) & (x['rule_name'] == rule_name)]

        # Plot 'act_amount' on the left y-axis with NaN for trigger field change
        for trigger_field, group in subset.groupby('action_type'):
            axes[i * len(x['method'].unique()) + j].plot(group['time'], group['act_amount'], label=f'Amount - Trigger {trigger_field}', linestyle=linestyle_dict[trigger_field], color='blue')

            # Add NaN to create a gap between trigger field changes
            axes[i * len(x['method'].unique()) + j].plot(group['time'].iloc[-1:], np.repeat([None], len(group['time'].iloc[-1:])), color='white')

        # Create a twin y-axis for 'duration' on the right
        axes2 = axes[i * len(x['method'].unique()) + j].twinx()
        axes2.plot(subset['time'], subset['duration'], label='Duration', color='green')

        # Set y-axis limits based on global max and min values
        axes[i * len(x['method'].unique()) + j].set_ylim([global_min_amount, global_max_amount])
        axes2.set_ylim([global_min_duration, global_max_duration])

        # Add column titles
        if i == 0:
            axes[j].set_title(method)

# Add row title
for i, rule_name in enumerate(x['rule_name'].unique()):
    axes[i * len(x['method'].unique())].set_ylabel(rule_name)

# Replace x-axis labels with scalar indices
for ax in axes[-len(x['method'].unique()):]:
    ax.set_xticks(range(len(x['time'].unique())))
    ax.set_xticklabels(range(len(x['time'].unique())))

# Adjust layout
plt.tight_layout(rect=[0, 0.03, 1, 0.95])

# Overall title
fig.suptitle('Amount and Duration Across Methods and Rules', fontsize=16)

# Combine legends and place at the top right
handles, labels = axes[0].get_legend_handles_labels()
fig.legend(handles ,labels, loc='upper right', bbox_to_anchor=(1, 1))

# Show the plot
plt.show()


In [ ]:
import gym
import custom_splunk
gym.make('splunk-v0')

In [ ]:
gym.envs.registry.keys()

In [ ]:
! pip install --upgrade matplotlib

In [ ]:
alt.Chart(time_rules_energy_df).mark_line(color='green', point=True).encode(
    x='index',
    y='duration',
    color='method',
    row='rule_name'

).properties(
    title='Energy consumption of the DRL method vs the baseline methods',
    width=800,
)

In [ ]:
alt.Chart(time_rules_energy_df.sort_values(by=['energy'], ascending=False)).mark_line(color='green', point=True).encode(
    x=alt.X('action_amount', sort=alt.EncodingSortField(field="energy", op="sum", order='ascending')),
    y='energy',
    color=alt.Color('rule_name', sort='-y', scale=alt.Scale(scheme='category20')),

)

In [ ]:
base = alt.Chart(time_rules_energy_df).encode(x='index')

# Chart for energy
e = base.mark_line(color='green').encode(
    y=alt.Y('energy', axis=alt.Axis(title='Energy', orient='left'))
)

# Chart for action amount with its own y-axis on the right
a = base.mark_line(color='blue').encode(
    y=alt.Y('action_amount', axis=alt.Axis(title='Action Amount', orient='right'))
)

# Combine the charts and facet them
chart = (e + a).facet(
    column='method',
    row='rule_name'
).resolve_scale(
    y='independent'
).properties(
    title='Energy consumption of the DRL method vs the baseline methods'
)

chart


In [ ]:
import xml.etree.ElementTree as ET
from socfaker import SocFaker
from lxml import etree

sc = SocFaker()
# log = sc.logs.windows.eventlog(1, event_code_list=[5140])
log = sc.logs.windows.sysmon(1, event_code_list=[3])
xml_data = b"<?xml version=\"1.0\" encoding=\"utf-8\" standalone=\"yes\"?>\n<Events>\n"
for event in log:
    event = event.encode("utf-8")
    event = etree.fromstring(event)
    xml_data += etree.tostring(event, encoding='utf8', method='xml')
    xml_data += b"\n"
xml_data += b"</Events>"
with open('xml_file_name2.xml', "wb") as fe:
        fe.write(xml_data)

In [ ]:
result_text

In [ ]:

''.format({'sd':1, 'sdf':2, 'sdf':3})

In [ ]:
import json

xml_data = sc.logs.windows.eventlog(1, event_code_list=[5140])

splunk_event = {
    "time": "2021-06-04T06:25:54.170835+03:00",
    "host": "Desktop-605IHDW",
    "source": "C:\\\\Documents",
    "event": xml_data[0]
}

print(json.dumps(splunk_event))

In [ ]:


import re
CPU_TDP = 200

path = '/home/shouei/GreenSecurity-FirstExperiment/SplunkResearch/VMware, Inc. Linux 3.10.0-1160.88.1.el7.x86_64/Splunk Enterprise SIEM/Power Saver Plan/One Scan'
last = 454
num_of_measurements = 16
rng = range(last-num_of_measurements+1, last+1 )
dirs = {f'Measurement {i}'for i in rng}
measurement_dirs = sorted([d for d in os.listdir(path) if d in dirs])
# measurement_dirs = sorted([d for d in os.listdir(path) if d.startswith('Measurement')])
dfs=[]
action_list = []
time_field = 'Time(sec)'
for measurement_dir in measurement_dirs:
    measurement_path = os.path.join(path, measurement_dir)
    rules_enegry_path = os.path.join(measurement_path, 'rules_energy.csv')
    rules_energy_df = pd.read_csv(rules_enegry_path)
    with open(os.path.join(measurement_path, 'action.txt'), 'r') as f:
        action = f.read()
    # transform the action string to a list of integers
    action = [i.strip('\n').strip(' ') for i in re.split(',| ',action[1:-1])]
    action = [int(i) for i in action if i != '']
    action_list.append(action)     
    if rules_energy_df.empty:
        continue
    print(measurement_dir)
    # create a new column for the time interval
    rules_energy_df[time_field] = pd.to_datetime(rules_energy_df[time_field])
    # Get start time
    start_time = rules_energy_df[time_field].min()
    rules_energy_df = rules_energy_df.sort_values(by=['name', time_field])
    # get difference between each time interval in seconds grouped by name
    rules_energy_df['delta_time'] = rules_energy_df.groupby('name')[time_field].diff().dt.total_seconds().fillna(0)
    # create a new column for the integral of the cpu using the trapezoidal rule
    # grouped_rules_energy_df = rules_energy_df.groupby('name').apply(lambda g: integrate.simpson(g['CPU(%)'], x=g['delta_time']))
    # grouped_rules_energy_df = grouped_rules_energy_df.reset_index().rename(columns={0: 'cpu_integral'})
    rules_energy_df['CPU(W)'] = rules_energy_df['CPU(%)'] * CPU_TDP / 100
    rules_energy_df['CPU(J)'] = rules_energy_df['CPU(W)'] * rules_energy_df['delta_time']
    grouped_rules_enegry_df = rules_energy_df.groupby('name')['CPU(J)'].sum().reset_index()
    # create a chart for the cpu usage using altair
    grouped_rules_enegry_df['measurement'] = measurement_dir
    dfs.append(grouped_rules_enegry_df)
action_df = pd.DataFrame(action_list, columns=log_types_str)
action_df['measurement'] = measurement_dirs
final_df = pd.concat(dfs)



In [ ]:
rules_energy_df.groupby('name')[time_field].diff().dt.total_seconds().fillna(0)

In [ ]:
# merge helper df with final df
final_df_with_action = pd.merge(final_df, action_df, left_on='measurement', right_on='measurement')
final_df_with_action['action'] =pd.Series([0]*len(final_df_with_action))
for measurement_dir in measurement_dirs:
    if final_df_with_action[final_df_with_action['measurement'] == measurement_dir].empty:
        continue
    if final_df_with_action[final_df_with_action['measurement'] == measurement_dir].loc[:,log_types_str].iloc[0].sum() > 0:
        final_df_with_action.loc[final_df_with_action['measurement'] == measurement_dir, 'action'] = 1

In [ ]:
unique_log_types = {x for y in logtypes_by_rule_dict.values() for x in y}
print(len(unique_log_types))
unique_log_types

In [ ]:
sums = []
for rule, measurement in final_df_with_action[['name', 'measurement']].values:
    try:
        sums.append(final_df_with_action[(final_df_with_action.name == rule)&(final_df_with_action.measurement == measurement)][logtypes_by_rule_dict[rule.lower()]].sum(axis=1).values[0])
    except:
        sums.append(0)
final_df_with_action['relevant_logs_addition'] = sums

In [ ]:
final_df_with_action

In [ ]:
chart = alt.Chart(final_df_with_action).mark_line(point=True).encode(
y=alt.Y('CPU(J):Q', axis=alt.Axis(title='CPU energy (J)')),
# row=alt.Column('name:N', header=alt.Header(orient='top', labelFontSize=20)),
color=alt.Color('name:N'),
x=alt.X('relevant_logs_addition:Q', axis=alt.Axis(title=None))
).properties(
title=f'CPU Energy Consumption'
)

chart

In [ ]:
chart = alt.Chart(final_df_with_action).mark_bar().encode(
y=alt.Y('cpu_integral:Q', axis=alt.Axis(title='CPU Integral')),
row=alt.Column('name:N', header=alt.Header(orient='top', labelFontSize=20)),
color=alt.Color('relevant_logs_addition:Q'),
x=alt.X('measurement:N', axis=alt.Axis(title=None))
).properties(
title=f'CPU Integral'
)

chart
# with alt.data_transformers.enable('default'):
#     chart.save(f'{measurement_path}/graph/cpu_integral.png', engine="altair_saver")
# chart.save(f'{measurement_path}/graphs/cpu_integral.html', embed_options={'renderer':'svg'})

In [ ]:
results = []
for rule in final_df['name'].unique():
    rule_logtypes = [f"{logtype[0].lower().replace('*', '')}_{logtype[1]}" for logtype in section_logtypes[rule]]
    rule_logtypes = [x.replace('\"', '') for x in rule_logtypes]
    try:
        tmp = final_df_with_action[final_df_with_action['name']==rule][rule_logtypes]
    except:
        tmp = pd.DataFrame()
    results.append(tmp)
logtypes_df = pd.concat(results, axis=1).sort_index()

logtypes_final_df = pd.merge(final_df, logtypes_df, left_index=True, right_index=True)


In [ ]:
logtypes_final_df['added_logs'] = logtypes_final_df.drop(columns=['name','cpu_integral','measurement']).sum(axis=1).astype(np.float64)
logtypes_final_df

In [ ]:
chart = alt.Chart(logtypes_final_df).mark_point().encode(
y=alt.Y('cpu_integral:Q', axis=alt.Axis(title='CPU Integral')),
row=alt.Column('name:N', header=alt.Header(orient='top', labelFontSize=20)),
x=alt.X('added_logs:Q', axis=alt.Axis(title=None))
).properties(
title=f'CPU Integral'
)
chart

In [ ]:
# load alert status
# load current distribution
alert_status_list = []
current_distribution_list = []
for measurement_dir in measurement_dirs:
    measurement_path = os.path.join(path, measurement_dir)
    alert_status_path = os.path.join(measurement_path, 'alerts_status.json')
    current_distribution_path = os.path.join(measurement_path, 'current_distribution.json')
    with open(alert_status_path, 'r') as f:
        alert_status = json.load(f)['results']
    with open(current_distribution_path, 'r') as f:
        current_distribution = json.load(f)
    alert_status_list.append(alert_status)
    current_distribution_list.append(current_distribution)

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt

# Define figure and axes
fig, ax = plt.subplots()
amount = 50

# Plot second dataframe on the same axis
df2 = pd.DataFrame(index=current_distribution_list[1].keys(), data=current_distribution_list[1].values(), columns=['Current Distribution'])
df2.index = df2.index.str.lower()
df2 = df2.reset_index().groupby('index').sum()
df2.drop(index='total_count').sort_values(by='Current Distribution', ascending=False).head(amount).plot(kind='bar', ax=ax, color='r', label='Current Distribution', alpha=0.5)

# Plot first dataframe on the defined axis
df1 = pd.DataFrame(index=current_distribution_list[0].keys(), data=current_distribution_list[0].values(), columns=['Wanted Distribution'])
df1.index = df1.index.str.lower()
df1 = df1.reset_index().groupby('index').sum()
df1.drop(index='total_count').sort_values(by='Wanted Distribution', ascending=False).head(amount).plot(kind='bar', ax=ax, color='b', label='Wanted Distribution', alpha=0.5)


# Add title and legend
plt.title('Wanted vs Current Log Types Distribution')
plt.legend()

# If needed, rotate x-axis ticks
ax.tick_params(axis='x', which='both', labelsize=5)

plt.show()



In [ ]:
diff = (df2['Current Distribution']-df1['Wanted Distribution']).drop(index='total_count').sort_values(ascending=False)
diff[diff>0].head(amount).plot(kind='bar', figsize=(20, 10), title='Difference between current distribution and wanted distribution')

In [ ]:
pd.DataFrame(alert_status_list[0]).groupby('savedsearch_name').count()

In [ ]:
rules_enegry_df[rules_enegry_df['name'] == 'An Account Was Logged off']

In [ ]:
charts[1]

Merge when the rules running one after an other with a delay

Merge when all the rules running in the same time

In [ ]:
relevant_processes_pid_names_grouped_dict = {}
relevant_processes_pid_names_mean_windows_dict = {}
relevant_names_inegral_dict = {}
path = '/home/shouei/GreenSecurity-FirstExperiment/VMware, Inc. Linux 3.10.0-1160.88.1.el7.x86_64/Splunk Enterprise SIEM/Power Saver Plan/One Scan'

# path = fr"../../Repositories/GreenSecurity-FirstExperiment/Dell Inc. Linux 5.15.0-70-generic/Splunk Enterprise SIEM/Power Saver Plan/One Scan/"
for measurment_name in measurement_dirs:
    pid_1_times = set(exp_dfs[measurment_name].groupby('pid').count().dropna().index)
    name_1_times = exp_dfs[measurment_name].where(lambda x: x.pid.isin(pid_1_times))[['name','pid']]
    relevant_processes = dfs[measurment_name].where(lambda x: x.PID.isin(pid_1_times))
    relevant_processes_pid_names = pd.merge(relevant_processes, name_1_times, left_on='PID', right_on='pid')
    
    # Get start time
    start_time = relevant_processes_pid_names['Time(sec)'].min()
    # Calculate delta time in seconds
    relevant_processes_pid_names['delta_time'] = (relevant_processes_pid_names['Time(sec)'] - start_time).dt.total_seconds()
    print(len(relevant_processes_pid_names)/relevant_processes_pid_names['delta_time'].max())
    #####Create a chart########
    # Create the dropdown menu selection
    name_selection = alt.selection_multi(fields=['name'], bind='legend')
    # Define the chart
    chart = alt.Chart(relevant_processes_pid_names).mark_line(interpolate='linear').encode(
            alt.Y("CPU(%):Q"),
            alt.X(f"delta_time:Q"),
            alt.Color('name:N', scale=alt.Scale(scheme='category20')),
            opacity=alt.condition(name_selection, alt.value(1), alt.value(0.1))
        ).properties(
            width=1500,
            height=500
        ).add_selection(name_selection).configure_legend(
            orient='bottom',
            labelLimit=10000,
            columns=4,
            labelFontSize=15
        )
    with alt.data_transformers.enable('default'):
        chart.save(f"{path}/{measurment_name}/graphs/interactive_line.html")
    ##########################
    
    #####Create a chart########
    rule_chart = alt.Chart(relevant_processes_pid_names).mark_rule(strokeDash=[5, 5]).encode(
    x='min(Time(sec)):T',color='name'
    )

    c2 = alt.Chart(relevant_processes_pid_names).mark_line(interpolate='linear').encode(
            alt.Y("CPU(%):Q"),
            alt.X(f"Time(sec):T"),
        ).properties(
            width=1000,
            height=500
        )
    mean_chart = alt.Chart(relevant_processes_pid_names).mark_rule(color='red', strokeDash=[5, 5]).encode(
        y='mean(CPU(%)):Q'
    )

    chart2 = (c2+rule_chart+mean_chart).configure_legend(
                labelLimit=10000,
                labelFontSize=15
            )
    with alt.data_transformers.enable('default'):
        chart2.save(f"{path}/{measurment_name}/graphs/total_cpu.html")
    ##########################
    
    relevant_processes_pid_names_grouped = relevant_processes_pid_names.groupby('name').mean()
    relevant_processes_pid_names_grouped_dict[measurment_name] = relevant_processes_pid_names_grouped
    #integral by name of cpu over time
    relevant_names_inegral_dict[measurment_name] = relevant_processes_pid_names.groupby('name').apply(lambda g: integrate.trapz(g['CPU(%)'], x=g['delta_time']))

    
    # # Define the time window size in minutes
    # time_window_size = 1
    # last_sec = int(np.ceil(relevant_processes_pid_names['delta_time'].max()))
    # # Create an empty column to store the mean values
    # relevant_processes_pid_names['mean_col'] = pd.Series()
    # relevant_processes_pid_names['time_window'] = pd.Series()

    # # Iterate over the time series data, and calculate the mean for each time window
    # for i in range(last_sec):
    #     start_time = i
    #     end_time = start_time + time_window_size
    #     window_data = relevant_processes_pid_names[(relevant_processes_pid_names['delta_time'] >= start_time) & (relevant_processes_pid_names['delta_time'] < end_time)]
    #     mean_values = window_data.groupby('name')['CPU(%)'].mean()
    #     for name in mean_values.index:
    #         relevant_processes_pid_names.loc[window_data[window_data['name']==name].index, 'mean_col'] = mean_values[mean_values.index==name][0]
    #         relevant_processes_pid_names.loc[window_data[window_data['name']==name].index, 'time_window'] = i
    
    relevant_processes_pid_names_mean_windows_dict[measurment_name] = relevant_processes_pid_names
    




In [ ]:
import itertools


times = ['12', '24', '36', '48', '60', '72']
field_state = ['disable', 'enable']
# num_of_experiments = 6
# create all the permutations of the times and field_state as concatinated strings
durations = [f"{field} {time}" for time, field in itertools.product(field_state, times)]
durations

In [ ]:
# pid_df = pd.DataFrame([[k]+s for k, v in pids[curr_measurement].items() for s in v], columns=['name', 'sid', 'pid', 'time', 'run_duration']) 
# pid_df.time = pd.to_datetime(pid_df.time)
# # group by time with 10 minutes interval and take the min value of each group
# pid_df.groupby(pd.Grouper(key='time', freq='10min')).min().index
# # pid_df.groupby('time').min()

In [ ]:
def get_searches_times(pid_dict):
    pid_df = pd.DataFrame([[k]+s[:4] for k, v in pid_dict.items() for s in v], columns=['name', 'sid', 'pid', 'time', 'run_duration'])        
    pid_df.time = pd.to_datetime(pid_df.time)
    # group by time with 10 minutes interval and take the min value of each group
    search_times = pid_df.groupby(pd.Grouper(key='time', freq='10min')).min().index
    return pid_df, search_times

In [ ]:
import subprocess
import datetime
import concurrent.futures
import json
os.makedirs("logs_types_info", exist_ok=True)
if not os.path.exists(f'logs_types_info/logs_len_list_{rng[0]}_{rng[-1]}.json'):
    dirs = {f'Measurement {i}' for i in rng}
    logs_len_list = {}
    j = rng[0]
    last_j = rng[-1]+1
    def run_command(command):
        cmd = subprocess.run(command, shell=True, capture_output=True, text=True)
        output = cmd.stdout
        print(output)
        # Parse the output to get the number.
        # num = int(output.split('\n')[2].strip()) if len(output.split('\n')) > 2 else output
        res_dict = {}
        if len(cmd.stdout.split('\n')) > 2:
            for row in cmd.stdout.split('\n')[2:-1]:
                row = row.split()
                source = row[0]
                event_code = row[1]
                count = row[2]
                total_count = row[3]
                res_dict[f"{source} {event_code}"] = int(count)
            res_dict['total_count'] = int(total_count)
        return res_dict

    with concurrent.futures.ThreadPoolExecutor() as executor:
        future_to_command = {}
        # for state in field_state:
        for time in times:
            curr_measurement = f"Measurement {j}"
            path = fr"./VMware, Inc. Linux 3.10.0-1160.88.1.el7.x86_64/Splunk Enterprise SIEM/Power Saver Plan/One Scan/{curr_measurement}"
            # convert pids values to df
            pid_df, search_times = get_searches_times(pids[curr_measurement])
            end_time = "06/15/2023:08:00:00"
            # end_time = datetime.datetime.strptime(end_time, '%m/%d/%Y:%H:%M:%S')
            start_time = time
            start_time = (datetime.datetime.strptime(end_time, '%m/%d/%Y:%H:%M:%S') - datetime.timedelta(hours=int(start_time.split('h')[0]))).strftime('%m/%d/%Y:%H:%M:%S')
            command = f'echo | sudo -S -E env "PATH=$PATH" splunk search "index=main (earliest="{start_time}" latest="{end_time}")|stats count by source EventCode | eventstats sum(count) as totalCount" -maxout 0 -auth shouei:'
            print(command)
            future_to_command[executor.submit(run_command, command)] = (command, time)   

            j += 1
            if j == last_j:                
                break
        for future in concurrent.futures.as_completed(future_to_command):
            command, time = future_to_command[future]
            try:
                data = future.result()
            except Exception as exc:
                print(f'{command} generated an exception: {exc}')
            else:
                logs_len_list[time] = data
    # save the logs_len_list to a json file
    with open(f'logs_types_info/logs_len_list_{rng[0]}_{rng[-1]}.json', 'w') as f:
        json.dump(logs_len_list, f)
else: 
    # load the logs_len_list from a json file
    with open(f'logs_len_list_{rng[0]}_{rng[-1]}.json', 'r') as f:
        logs_len_list = json.load(f)

In [ ]:
import pytz


dirs = {f'Measurement {i}'for i in rng}
integral_list = []
j = rng[0]
i = 0
for state in field_state:
    for time in times:
        # for i in range(num_of_experiments):
        curr_measurement = f"Measurement {j}"
        path = fr"./VMware, Inc. Linux 3.10.0-1160.88.1.el7.x86_64/Splunk Enterprise SIEM/Power Saver Plan/One Scan/{curr_measurement}"
        pid_df, search_times = get_searches_times(pids[curr_measurement])
        g_pid_df = pid_df.groupby(['name', pd.Grouper(key='time', freq='10min')]).min().reset_index()
        for rule_name, val in pids[curr_measurement].items():
            curr_df = relevant_processes_pid_names_mean_windows_dict[curr_measurement]
            curr_df = curr_df[(curr_df['name']==rule_name)]
            if curr_df.empty:
                print(curr_measurement, rule_name)
                continue
            curr_df.loc[:, 'Time(sec)'] = curr_df['Time(sec)'].dt.to_pydatetime()
            curr_df.loc[:, 'Time(sec)'] = curr_df['Time(sec)'].dt.tz_localize('UTC')
            # define the first time of the world
            # date_time = datetime.datetime.fromtimestamp(0, tz=datetime.timezone.utc)
            # s_times = g_pid_df[g_pid_df.name==rule_name].dropna()[['time', 'pid']]
            for v in val:
                # print(j, i)
                # convert v[3] (str date) to datetime in utc
                date_time = datetime.datetime.strptime(v[4], '%Y-%m-%d %H:%M:%S')
                jerusalem = pytz.timezone('Asia/Jerusalem')
                date_time = jerusalem.localize(date_time)
                date_time = date_time.astimezone(pytz.UTC)
                # date_time = datetime.datetime.strptime(v[2], '%Y-%m-%d %H:%M:%S.%f IDT')
                
                # date_time = date_time.replace(hour=date_time.hour-3)
                
                # target_timezone = pytz.timezone('UTC')
                # date_time = date_time.astimezone(target_timezone)
                duration = datetime.timedelta(seconds=v[3])
                name_integral = {}
                pid = v[1]
                # s_time = s_times[s_times.pid==pid].time.values[0]
                df_section = curr_df[(curr_df['pid']==pid)]

                df_section = df_section[(df_section['Time(sec)']>date_time)&(df_section['Time(sec)']<=date_time+duration)]
                if df_section.empty:
                    print(curr_measurement, rule_name, v)
                    continue
                bug = df_section[df_section['WRITE_IO(KB)']<0]
                df_section = df_section.drop(bug.index)
                # if not bug.empty:
                #     print(df_section)
                #     df_section = df_section.loc[:bug.index[0]-1]
                #     print(df_section)
                # df_section['delta_diff'] = df_section['delta_time'].diff()
                # df_section.drop(df_section[df_section['delta_diff']>10].index, inplace=True)
                # df_section = curr_df[(curr_df['Time(sec)']>date_time)]
                # min_date_time = df_section['Time(sec)'].min()
                # df_section = df_section[(df_section['Time(sec)']<=min_date_time+duration)]
                integral_cpu= integrate.simpson(df_section['CPU(%)'], x=df_section['delta_time'])
                disk_w_q= df_section['WRITE_IO(#)'].sum()
                disk_r_q= df_section['READ_IO(#)'].sum()
                disk_w_k= df_section['WRITE_IO(KB)'].sum()
                disk_r_k= df_section['READ_IO(KB)'].sum()
                # integral_disk_w_q= integrate.simpson(df_section['WRITE_IO(#)'], x=df_section['delta_time'])
                # integral_disk_r_q= integrate.simpson(df_section['READ_IO(#)'], x=df_section['delta_time'])
                # integral_disk_w_k= integrate.simpson(df_section['WRITE_IO(KB)'], x=df_section['delta_time'])
                # integral_disk_r_k= integrate.simpson(df_section['READ_IO(KB)'], x=df_section['delta_time'])
                # name_integral[name] = (integral, logs_len_list[i])
                integral_list.append((integral_cpu,disk_w_q,disk_r_q,disk_w_k,disk_r_k, logs_len_list[time]['total_count'], v[3], time, curr_measurement, state, rule_name, pid))
                # date_time = df_section['Time(sec)'].max()
                i += 1
                # print(min_date_time, duration, date_time)
        j += 1


In [ ]:
# list comprehnsion to get the amount of searches
[len([x for v in pids[f'Measurement {i}'].values() for x in v]) for i in rng]

# [x  for x in v for r,v in pids[m].items()  for m in measurement_dirs]

In [ ]:
df = pd.DataFrame(integral_list, columns=['integral_cpu','disk_w_q','disk_r_q','disk_w_k','disk_r_k','logs_number', 'duration', 'time_range', 'measurment_num', 'state', 'rule_name','pid'])
df = df[df['logs_number'] != '']
# df['normalized_integral'] = df['integral']/df['logs_number']
df

In [ ]:
logs_len_dfs = []
for k in logs_len_list:
    source_event_df = pd.DataFrame.from_dict(logs_len_list[k],orient='index', columns=['count']).iloc[:-1]
    source_event_df = source_event_df.reset_index().rename({'index':'source_event'}, axis=1)
    source_event_df[['source','event_code']] = pd.DataFrame(source_event_df['source_event'].apply(lambda x: x.split()).tolist())
    # delete the the lines that are not numbers
    source_event_df = source_event_df[source_event_df['event_code'].str.isnumeric()]
    source_event_df['event_code'] = source_event_df['event_code'].astype(int)
    source_event_df[['source_type','log_name']] = pd.DataFrame(source_event_df['source'].apply(lambda x: x.split(':')).tolist())
    source_event_df['time_range'] = k
    logs_len_dfs.append(source_event_df)
logs_len_df = pd.concat(logs_len_dfs)

In [ ]:
source_event_df['event_code']

In [ ]:
alt.Chart(logs_len_df).mark_line().encode(
    alt.X('time_range:N'),
    alt.Y('mean(count):Q'),
    alt.Color('log_name:N', scale=alt.Scale(scheme='category10')),
).properties(
    width=600,
    height=300
)

In [ ]:

logs_len_df

In [ ]:
alt.Chart(logs_len_df[logs_len_df['log_name']=='Microsoft-Windows-Sysmon/Operational']).mark_arc().encode(
    alt.Color('event_code:N', scale=alt.Scale(scheme='category10')),
    alt.Theta('mean(count):Q'),
)

In [ ]:
sysmon_logs_amount = logs_len_df[logs_len_df['log_name']=='Microsoft-Windows-Sysmon/Operational'].groupby(['time_range','event_code']).sum().reset_index()
sysmon_logs_amount

In [ ]:
sysmon_logs_amount

In [ ]:
Detected_Registry_Modification_df = df[df['rule_name']=='Detected Registry Modification']
Detected_Registry_Modification_df = Detected_Registry_Modification_df.merge(sysmon_logs_amount, on='time_range')
Detected_Registry_Modification_df['normalized_integral_cpu'] = Detected_Registry_Modification_df['integral_cpu']/Detected_Registry_Modification_df['count']

In [ ]:
Detected_Registry_Modification_df

In [ ]:
Detected_Registry_Modification_df['normalized_integral_cpu'].describe()

In [ ]:
# show 10 lines of df
pd.set_option('display.max_rows', 50)
df.groupby(['rule_name']).mean().max()
# df.groupby(['rule_name','time_range','state']).count().describe()


In [ ]:
# alt scatters chart of df, shape is time range, x is duration, y is integral, color is rule name and columns is state
alt.Chart(df).mark_circle().encode(
    alt.X('mean(disk_r_k):Q'),
    # alt.X('duration:Q'),
    alt.Y('mean(integral_cpu):Q'),
    alt.Size('mean(duration):Q'),
    alt.Color('rule_name:N', scale=alt.Scale(scheme='category20')),
    # alt.Shape('state:N'),
    alt.Tooltip(['rule_name']),
).properties(
    width=600,
    height=200,
    title='CPU vs Disk KB'
).configure_legend(
    labelLimit=10000,
    labelFontSize=10
)

In [ ]:
# alt scatters chart of df, shape is time range, x is duration, y is integral, color is rule name and columns is state
alt.Chart(df).mark_circle(size=20).encode(
    alt.X('mean(disk_r_q):Q'),
    # alt.X('duration:Q'),
    alt.Y('mean(integral_cpu):Q'),
    alt.Size('mean(duration):Q'),
    alt.Color('rule_name:N', scale=alt.Scale(scheme='category20')),
    # alt.Shape('state:N'),
    alt.Tooltip(['rule_name']),
).properties(
    width=600,
    height=200,
    title='CPU vs Disk #'
).configure_legend(
    labelLimit=10000,
    labelFontSize=10
)

In [ ]:
alt.Chart(df).mark_bar().encode(
    alt.Y("sum(disk_r_k):Q", title='Disk read by KB'),
    alt.X(f"time_range:N"),
    # alt.Column('rule_name:N'),
    alt.Color('rule_name:N', scale=alt.Scale(scheme='category20')),
    # column='time_range:N'
).properties(
    width=300,
    height=300,
    title='Disk read by KB'
).configure_legend(
    labelLimit=10000,
    labelFontSize=10
)

In [ ]:
alt.Chart(df).mark_bar().encode(
    alt.Y("mean(disk_r_q):Q"),
    alt.X(f"time_range:N"),
    # alt.Column('rule_name:N'),
    alt.Color('rule_name:N', scale=alt.Scale(scheme='category20')),
    # column='time_range:N'
).properties(
    width=300,
    height=300,
    title='Disk #'
).configure_legend(
    labelLimit=10000,
    labelFontSize=10
)

In [ ]:
alt.Chart(df).mark_bar().encode(
    alt.Y("mean(integral_cpu):Q", title='CPU Usage (Integral over time)'),
    alt.X(f"time_range:N"),
    # alt.Column('rule_name:N'),
    alt.Color('rule_name:N', scale=alt.Scale(scheme='category20')),
    # column='time_range:N'
).properties(
    width=300,
    height=300,
    title='CPU Integral'
).configure_legend(
    labelLimit=10000,
    labelFontSize=10
)

In [ ]:
alt.Chart(df).mark_bar().encode(
    alt.Y("mean(integral):Q"),
    alt.X(f"state:N"),
    alt.Row('rule_name:N'),
    # alt.Color('rule_name:N', scale=alt.Scale(scheme='category20')),
    column='time_range:N'
).properties(
    width=100,
    height=300
).configure_legend(
    labelLimit=10000,
    labelFontSize=10
)

In [ ]:
# step = 1

# dirs = {f'Measurement {i}'for i in rng}
# for i in rng:
#     if i == step:
#         break
#     first_measurment = f'Measurement {i}'
#     sec_measurment = f'Measurement {i+step}'
#     first_relevant_processes_pid_names = relevant_processes_pid_names_mean_windows_dict[first_measurment]
#     sec_relevant_processes_pid_names = relevant_processes_pid_names_mean_windows_dict[sec_measurment]
    
#     rule_chart_first = alt.Chart(first_relevant_processes_pid_names).mark_rule(strokeDash=[5, 5]).encode(
#         x='min(delta_time):Q',color='name'
#     )

#     c2_first = alt.Chart(first_relevant_processes_pid_names).mark_line(interpolate='linear').encode(
#             alt.Y("CPU(%):Q"),
#             alt.X(f"delta_time:Q"),
#         ).properties(
#             width=1000,
#             height=500
#         )
#     mean_chart_first = alt.Chart(first_relevant_processes_pid_names).mark_rule(color='blue', strokeDash=[5, 5]).encode(
#         y='mean(CPU(%)):Q'
#     )
#     rule_chart_sec = alt.Chart(sec_relevant_processes_pid_names).mark_rule(strokeDash=[5, 5]).encode(
#         x='min(delta_time):Q',color='name'
#     )

#     c2_sec = alt.Chart(sec_relevant_processes_pid_names).mark_line(color='red',interpolate='linear').encode(
#             alt.Y("CPU(%):Q"),
#             alt.X(f"delta_time:Q"),
#         ).properties(
#             width=1000,
#             height=500
#         )
#     mean_chart_sec = alt.Chart(sec_relevant_processes_pid_names).mark_rule(color='red', strokeDash=[5, 5]).encode(
#         y='mean(CPU(%)):Q'
#     )
#     with alt.data_transformers.enable('default'):
#         (c2_first+rule_chart_first+mean_chart_first+c2_sec+rule_chart_sec+mean_chart_sec).configure_legend(
#                 labelLimit=10000,
#                 labelFontSize=15
#             ).save(f"{path}/{measurment_name}/graphs/compare_cpu.html")

In [ ]:
# # create histogram with mean rule
# hist = alt.Chart(first_relevant_processes_pid_names).mark_bar(color='red', opacity=0.2).encode(
#     alt.X('CPU(%)', bin=alt.Bin(step=0.2)),
#     y='count()'
# )

# mean_rule = alt.Chart(first_relevant_processes_pid_names).mark_rule(color='red').encode(
#     x='mean(CPU(%))'
# )
# # create histogram with mean rule
# hist_sec = alt.Chart(sec_relevant_processes_pid_names).mark_bar(color='green', opacity=0.2).encode(
#     alt.X('CPU(%)', bin=alt.Bin(step=0.2)),
#     y='count()'
# )

# mean_rule_sec = alt.Chart(sec_relevant_processes_pid_names).mark_rule(color='green').encode(
#     x='mean(CPU(%))'
# )

# # combine the two charts
# # combine the two charts and add a legend
# chart = alt.layer(hist, mean_rule, hist_sec, mean_rule_sec).properties(
#     title='Histogram of CPU',
#     width=500,
#     height=300
# )
# chart.configure_axis(
#     gridOpacity=0.5
# ).configure_view(
#     strokeWidth=0
# ).configure_title(
#     fontSize=20,
#     fontWeight='bold'
# ).configure_legend(
#     title=None,
#     labelFontSize=15
# )


In [ ]:
# relevant_processes_pid_names.apply(lambda g: integrate.trapz(g['CPU(%)'], x=g['delta_time']), axis=1)


In [ ]:
# # concatenate the three data frames along the columns axis
# merged_df_line = pd.concat([x.groupby(['name','time_window'])[['mean_col']].mean() for x in relevant_processes_pid_names_mean_windows_dict.values()], axis=1)
# durations = [1,2,3,4]
# num_of_different_durations = len([x for x in durations])
# # select even and odd columns from the 'CPU(%)' columns
# mean_std_df_line = pd.concat([merged_df_line.iloc[:, i::num_of_different_durations].agg(['mean', 'std'], axis=1).add_suffix('_'+str(durations[i])) for i in range(num_of_different_durations)], axis=1)
# # mean_std_df.iloc[:, 0:2].columns = mean_std_df.iloc[:, 0:2].add_suffix('_odd').columns
# # mean_std_df.iloc[:, 2:4].columns = mean_std_df.iloc[:, 2:4].add_suffix('_even').columns
# # print the final dataframe
# # mean_std_df_line.fillna(0, inplace=True)
# mean_std_df_line


In [ ]:
# mean_df_line = mean_std_df_line[[x for x in mean_std_df_line.columns if x.startswith('mean')]].reset_index().melt(var_name='duration',id_vars='time_window')
# std_df_line =mean_std_df_line[[x for x in mean_std_df_line.columns if x.startswith('std')]].reset_index().melt(var_name='duration',id_vars='time_window')
# mean_df_line[['kind', 'duration']] = mean_df_line.duration.str.split('_', expand=True)
# std_df_line[['kind', 'duration']] = std_df_line.duration.str.split('_', expand=True)

In [ ]:
# df_merged_mean_std = pd.merge(mean_df_line, std_df_line, on=['time_window', 'duration'])
# df_merged_mean_std

In [ ]:
# # reshape dataframe using pivot
# df_pivot = df_merged_mean_std.pivot(index=['time_window', 'duration'], columns=['kind_x','kind_y'], values=['value_x', 'value_y']).reset_index()

# # rename columns
# df_pivot.columns = ['time_window', 'duration', 'mean', 'std']

# print(df_pivot)

In [ ]:
# df_pivot['minus_std'] = df_pivot['mean'] + (-1) * df_pivot['std']
# df_pivot['pluse_std'] = df_pivot['mean'] + df_pivot['std']

In [ ]:
# name_selection = alt.selection_multi(fields=['duration'], bind='legend')
# lines = alt.Chart(df_pivot).mark_line().encode(
#             alt.Y("mean:Q",title='Mean CPU(%)'),
#             alt.X(f"time_window:Q"),
#             alt.Color('duration:N'),
#             opacity=alt.condition(name_selection, alt.value(1), alt.value(0.1)),
#         ).transform_filter(
#     'isValid(datum.mean)'
# )

# # Create the shaded area for the standard deviation
# band = alt.Chart(df_pivot).mark_errorband().encode(
#     alt.Y("pluse_std:Q"),
#     alt.Y2("minus_std:Q"),
#     alt.X(f"time_window:Q"),
#     alt.Color('duration:N'),
#     opacity=alt.condition(name_selection, alt.value(0.2), alt.value(0.02)),
#     # yError="std:Q"
# )
# final_chart = (lines + band).properties(
#             width=1500,
#             height=500,
#             title="Mean and Std CPU usage along the time over 4 duration"
#         ).add_selection(name_selection).configure_legend(
#             labelLimit=10000,
#             columns=4,
#             labelFontSize=15
#         )

In [ ]:
# with alt.data_transformers.enable('default'):
#     final_chart.save(f"interactive_line_all.html")

Merge when all the experiments were ran for the same duration

In [ ]:
# # concatenate the three data frames along the columns axis
# merged_df = pd.concat([x[['CPU(%)']] for x in relevant_processes_pid_names_grouped_dict.values()], axis=1)
# # compute the mean along the index axis
# mean_std_df = merged_df.agg(['mean', 'std'],axis=1)
# print(f"Num of rules: {len(mean_std_df)}")
# mean_std_df

Merge between the same duration

In [ ]:
# concatenate the three data frames along the columns axis
merged_df = pd.concat([x[['CPU(%)']] for x in relevant_processes_pid_names_grouped_dict.values()], axis=1)
# num_of_different_durations = len([x for x in durations])
# select even and odd columns from the 'CPU(%)' columns
cpus = []
for j, state in enumerate(field_state):
    for k, time in enumerate(times):
        cpus.extend([merged_df.iloc[:, (((i+1)*(j+1)*(k+1)-1) for i in range(num_of_experiments))].agg(['mean', 'std'], axis=1).add_suffix('_'+str(time)+' '+str(state))])
mean_std_df = pd.concat(cpus, axis=1)
# mean_std_df = pd.concat([merged_df.iloc[:, i::num_of_experiments*2].agg(['mean', 'std'], axis=1).add_suffix('_'+str(times[i])) for i in range(times)], axis=1)
# mean_std_df.iloc[:, 0:2].columns = mean_std_df.iloc[:, 0:2].add_suffix('_odd').columns
# mean_std_df.iloc[:, 2:4].columns = mean_std_df.iloc[:, 2:4].add_suffix('_even').columns
# print the final dataframe
mean_std_df


In [ ]:
mean_df =  mean_std_df.iloc[:, 0::2]
std_df = mean_std_df.iloc[:, 1::2]

In [ ]:
# split name column to duration and state
mean_df = mean_df.T.reset_index()
std_df = std_df.T.reset_index()
mean_df[['duration', 'state']] = mean_df['index'].str.split(' ', expand=True)
std_df[['duration', 'state']] = std_df['index'].str.split(' ', expand=True)


In [ ]:
# plot stacked bar chat with mean and std for each duration and state
mean_df = mean_df.drop(columns=['index'])
std_df = std_df.drop(columns=['index'])
mean_df = mean_df.set_index(['duration', 'state'])
std_df = std_df.set_index(['duration', 'state'])
mean_df = mean_df.stack().reset_index()
std_df = std_df.stack().reset_index()
mean_df.columns = ['duration', 'state', 'rule', 'value']
std_df.columns = ['duration', 'state', 'rule', 'value']
mean_df['rule'] = mean_df['rule'].str.strip('_mean')
std_df['rule'] = std_df['rule'].str.strip('_std')


    
    

In [ ]:
alt.Chart(mean_df).mark_bar().encode(
    alt.Y("value:Q"),
    alt.X(f"state:N"),
    alt.Color('rule:N', scale=alt.Scale(scheme='category20')),
    column='duration:N'
).properties(
    width=100,
    height=300
)
    

In [ ]:
# Set up the figure
# fig, ax = plt.subplots()
# df_to_plot = mean_std_df.reset_index().fillna(0)
# df_to_plot['std_15'] = df_to_plot['std_15'].astype(float)
# df_to_plot['std_30'] = df_to_plot['std_30'].astype(float)
# Plot the bars with error bars
for i in range(len(field_state)):  
    # ax = mean_std_df.reset_index()[["name"]+mean_cols].plot(x="name", kind="bar",capsize=4, rot=0, figsize=(20,9))
    ax = mean_df.iloc[:, len(times)*i:len(times)*(i+1)].reset_index().plot(x="duration", yerr=std_df.iloc[:, len(times)*i:len(times)*(i+1)].T.values, kind="bar", ,capsize=4, rot=0, figsize=(20,9))
    # ax.bar(mean_std_df.reset_index()['name'], mean_std_df.reset_index()[['mean_0','mean_1']], capsize=5)
    # plt.rcParams["figure.figsize"] = (20, 9)
    # Add axis labels and title
    ax.set_xlabel('Rule Name')
    ax.set_ylabel('Mean CPU(%)')
    ax.set_title('Bar chart with standard deviation error bars')
    # Rotate x-axis labels
    plt.xticks(rotation=45, ha='right')

    # Show the plot
    plt.show()


In [ ]:
relevant_processes_pid_names.groupby('name').apply(lambda g: integrate.trapz(g['CPU(%)'], x=g['delta_time']))

In [ ]:
relevant_processes_pid_names.values

In [ ]:
# concatenate the three data frames along the columns axis
merged_df = pd.concat([x for x in relevant_names_inegral_dict.values()], axis=1)
durations = [1]
num_of_different_durations = len([x for x in durations])
# select even and odd columns from the 'CPU(%)' columns
mean_std_df = pd.concat([merged_df.iloc[:, i::num_of_different_durations].agg(['mean', 'std'], axis=1).add_suffix('_'+str(durations[i])) for i in range(num_of_different_durations)], axis=1)
# mean_std_df.iloc[:, 0:2].columns = mean_std_df.iloc[:, 0:2].add_suffix('_odd').columns
# mean_std_df.iloc[:, 2:4].columns = mean_std_df.iloc[:, 2:4].add_suffix('_even').columns
# print the final dataframe
mean_std_df

In [ ]:

# Set up the figure
# fig, ax = plt.subplots()
# df_to_plot = mean_std_df.reset_index().fillna(0)
# df_to_plot['std_15'] = df_to_plot['std_15'].astype(float)
# df_to_plot['std_30'] = df_to_plot['std_30'].astype(float)
# Plot the bars with error bars
mean_cols = [f"mean_{i}" for i in durations]
std_cols = [f"std_{i}" for i in durations]
ax = mean_std_df.reset_index()[["name"]+mean_cols].plot(x="name", yerr=mean_std_df[std_cols].T.values, kind="bar", rot=0, capsize=4, figsize=(20,9))
# ax.bar(mean_std_df.reset_index()['name'], mean_std_df.reset_index()[['mean_0','mean_1']], capsize=5)
# plt.rcParams["figure.figsize"] = (20, 9)
# Add axis labels and title
ax.set_xlabel('Rule Name')
ax.set_ylabel('Mean Integral')
ax.set_title('Integral of CPU over Time (Mean and Std)')
# Rotate x-axis labels
plt.xticks(rotation=45, ha='right')

# Show the plot
plt.show()

In [ ]:
df.integral[0]

In [ ]:
sum_df = df
sum_df['sum_integral'] = df.integral.apply(lambda x: sum(x.values()))

In [ ]:
sum_df

In [ ]:
df_group = sum_df.groupby(['duration','kind']).agg(['mean','std'])
df_group.columns = df_group.columns.to_flat_index()
df_group = df_group.reset_index()
df_group.columns = ['duration', 'kind','logs_number_mean','logs_number_std','sum_integral_mean','sum_integral_std']
df_group

In [ ]:
df_group['logs_number_std2'] = df_group['logs_number_mean']-df_group.logs_number_std/2
df_group['logs_number_std'] = df_group['logs_number_mean']+df_group.logs_number_std/2
df_group['sum_integral_std2'] = df_group['sum_integral_mean']-df_group.sum_integral_std/2
df_group['sum_integral_std'] = df_group['sum_integral_mean']+df_group.sum_integral_std/2
df_group

In [ ]:
line = alt.Chart(df_group).mark_line(point=True).encode(
            alt.Y("sum_integral_mean:Q",title='Sum CPU(%) Integral over Time'),
            alt.X(f"logs_number_mean:Q",title='Count of ingested logs quantity'),
        ).properties(
    width=1000,
    height=400,
    title=''
)
line

In [ ]:
x

In [ ]:
sum_df

In [ ]:
x = sum_df.pivot_table(columns=['kind'], index=['logs_number','duration'], values='sum_integral').reset_index().groupby('duration').agg(['mean','std']).fillna(0)
x.columns = x.columns.to_flat_index()
x.columns = ['logs_number_mean','logs_number_std','heavy_sum_integral_mean','heavy_sum_integral_std','lite_sum_integral_mean','lite_sum_integral_std']

In [ ]:
x.plot(x='logs_number_mean',y=['lite_sum_integral_mean', 'heavy_sum_integral_mean'], yerr=x[['lite_sum_integral_std', 'heavy_sum_integral_std']], capsize=40)

In [ ]:
import altair as alt

# Melt the dataframe to long format
df_long = df_group.melt(id_vars=['duration', 'kind'])

# Define the base chart with faceting
base_chart = alt.Chart(df_long).mark_line(point=True).encode(
    alt.Y('value:Q', title='Mean and Standard Deviation'),
    alt.X('logs_number:Q'),
    alt.Color('kind:N'),
    facet=alt.Facet('stat:N', title=None, columns=2),
)

# Add error bars to each panel
error_bars_chart = base_chart.mark_errorbar().encode(
    y='value:Q',
    yError='stderr:Q',
)

# Calculate the standard error of the mean for each group
stderr = df_group.groupby(['duration', 'kind']).agg('std') / df_group.groupby(['duration', 'kind']).agg('count')

# Layer the error bars on top of the base chart
chart = (base_chart + error_bars_chart).transform_calculate(
    stderr=alt.datum['std'] / alt.datum['count']**0.5
).properties(
    title='Mean and Standard Deviation with Error Bars'
)

chart.show()


In [ ]:
df.groupby(['duration','kind']).plot(x='logs_number', y='integral',kind='bar')

In [ ]:
import requests
from time import sleep

# Define the Splunk URL and login credentials
url = "https://132.72.81.185:8089/servicesNS/shoueii/splunkawssecuritymon/saved/searches/"
username = "shoueii"
password = ""

# Define the list of scheduled search names to enable/disable
searches_to_enable = ['aws_detect_cloudtrail_trail_deleted Clone1', 'aws_detect_cloudwatch_log_group_delete Clone1', 'aws_detect_cloudwatch_log_stream_delete Clone1', 'aws_detect_ec2_instances_run Clone1', 'aws_detect_ec2_vpc_flow_config_deleted Clone1', 'aws_detect_ecr_image_auth_token_get Clone1']
searches_to_disable = ['aws_detect_iam_user_deleted Clone', 'aws_detect_iam_user_created Clone', 'aws_detect_iam_new_policy_version_assignment Clone', 'aws_detect_iam_group_added_with_user_from_ec2 Clone', 'aws_detect_ecr_new_repo_image_create Clone', 'aws_detect_ec2_ssh_public_key_addition Clone']


for search_name in searches_to_enable:
    # Define the headers and payload for the request
    headers = {"Content-type": "application/json"}
    payload = {"disabled": 0}

    # Make the request to update the scheduled search
    response = requests.post(
        url + search_name + "/",
        headers=headers,
        auth=(username, password),
        data=payload,
        verify=False,
    )
    sleep(2)
    # Check the response status code
    if response.status_code == 200:
        print("Scheduled search updated successfully")
    else:
        print("Error updating scheduled search")
        print(response.content)
    

# Loop through the list of searches to disable and disable them
for search_name in searches_to_disable:
   # Define the headers and payload for the request
    headers = {"Content-type": "application/json"}
    payload = {"disabled": 1}

    # Make the request to update the scheduled search
    response = requests.post(
        url + search_name + "/",
        headers=headers,
        auth=(username, password),
        data=payload,
        verify=False,
    )

    # Check the response status code
    if response.status_code == 200:
        print("Scheduled search updated successfully")
    else:
        print("Error updating scheduled search")
        print(response.content)
    

In [ ]:
import altair as alt
import pandas as pd
alt.data_transformers.enable('csv')

In [ ]:
import altair as alt
import pandas as pd
df = pd.read_csv('data_summary.csv')
df_dtsplunk = df[df['host']=='dt-splunk']
df = df[df['host']!='dt-splunk']
# create stacked bar chart with x axis tilted 45 degrees
chart = alt.Chart(df).mark_bar().encode(
    alt.X('host:N', title='Host name'),
    alt.Y('count:Q', title='Logs count'),
    alt.Color('sourcetype:N', title='Log sourcetype'),
).properties(
    width=1500,
    height=300,
    title='24 hours Logs count per host and sourcetype'
).configure_axis(
    labelFontSize=8,
    titleFontSize=20,
    labelAngle=45
)
chart

In [ ]:
df = pd.read_csv('eventtype_host.csv')
# create stacked bar chart with x axis tilted 45 degrees
chart = alt.Chart(df).mark_bar().encode(
    alt.X('host:N', title='Host name'),
    alt.Y('count:Q', title='Logs count'),
    alt.Color('eventtype:N', title='Log eventtype'),
).properties(
    width=1500,
    height=300,
    title='Last week Logs count per host and eventtype'
).configure_axis(
    labelFontSize=8,
    titleFontSize=20,
    labelAngle=45
)
chart

In [ ]:
df

In [ ]:
# find all the hosts that starts with 'dt'
df = pd.read_csv('eventtype_host.csv')
df = df[df['host'].str.startswith('DT')]
# create stacked bar chart with x axis tilted 45 degrees
chart = alt.Chart(df).mark_bar().encode(
    alt.X('host:N', title='Host name'),
    alt.Y('count:Q', title='Logs count'),
).properties(
    width=1500,
    height=300,
    title='One week Logs count per host and sourcetype'
).configure_axis(
    labelFontSize=8,
    titleFontSize=20,
    labelAngle=45
)
chart

In [ ]:
df = pd.read_csv('eventtype_hour_30.csv')
df.hour = pd.to_datetime(df.hour)
# create stacked bar chart with x axis tilted 45 degrees
chart = alt.Chart(df).mark_bar().encode(
    alt.X('hours(hour):T', title='Hour'),
    alt.Y('count:Q', title='Logs count'),
    alt.Color('eventtype:N', title='Log event type',sort=alt.SortField(field='count', order='descending')),
)
# add rule lines for sign the days
rule = alt.Chart(df).mark_rule(color='red', strokeDash=[5, 5]).encode(
    x='day:T'
).transform_timeunit(
    day='yearmonthdate(hour)'
)
(chart).properties(
    width=1500,
    height=300,
    title='Last month Logs count per event type'
).configure_axis(
    labelFontSize=15,
    titleFontSize=20,
    labelAngle=45
)


In [ ]:
df = pd.read_csv('eventtype_hour_30.csv')
df.hour = pd.to_datetime(df.hour)
# create stacked bar chart with x axis tilted 45 degrees
chart = alt.Chart(df).mark_bar().encode(
    alt.X('day(hour):T', title='Day'),
    alt.Y('mean(count):Q', title='Logs count'),
    alt.Color('eventtype:N', title='Log event type',sort=alt.SortField(field='count', order='descending')),
)
# add rule lines for sign the days
rule = alt.Chart(df).mark_rule(color='red', strokeDash=[5, 5]).encode(
    x='day:T'
).transform_timeunit(
    day='yearmonthdate(hour)'
)
(chart).properties(
    width=1500,
    height=300,
    title='Last month Logs count per event type'
).configure_axis(
    labelFontSize=15,
    titleFontSize=20,
    labelAngle=45
)


In [ ]:
df

In [ ]:
chart = alt.Chart(df).mark_line().encode(
    alt.X('yearmonthdate(hour):T', title='Hour'),
    alt.Y('mean(count):Q', title='Logs count'),
    alt.Color('eventtype:N', title='Log event type'),
)
# add rule lines for sign the days
rule = alt.Chart(df).mark_rule(color='red', strokeDash=[3, 3]).encode(
    x='day:T'
).transform_timeunit(
    day='yearmonthdate(hour)'
)
(chart+rule).properties(
    width=1500,
    height=300,
    title='Last month Logs count per event type'
).configure_axis(
    labelFontSize=15,
    titleFontSize=20,
    labelAngle=45
)

In [ ]:
df[df.hour.dt.hour==7].groupby('eventtype').sum().sort_values('count', ascending=False)

In [ ]:
# make pie chart from dt splunk
pie_chart = alt.Chart(df[df.hour.dt.hour==7]).mark_arc().encode(
    alt.Theta('count:Q', title='Logs count'),
    alt.Color('eventtype:N', title='Log eventtype',sort=alt.SortField(field='count', order='descending')),
).properties(
    width=800,
    height=800,
    title='Last month 7 am count per sourcetype'
)
pie_chart

In [ ]:
# make pie chart from dt splunk
df = pd.read_csv('eventtype_source.csv')
chart = alt.Chart(df).mark_bar().encode(
    alt.Color('eventtype:N', title='Log eventtype'),
    alt.Y('count:Q', title='Logs count'),
    alt.X('source:N', title='source'),
).properties(
    width=1000,
    height=800,
    title='Last week DT-Splunk host Logs count per eventtype'
).configure_axis(
    labelFontSize=15,
    titleFontSize=20,
    labelAngle=45
).configure_legend(
    labelFontSize=15
)
chart

In [ ]:
# make pie chart from dt splunk
pie_chart = alt.Chart(df_dtsplunk).mark_arc().encode(
    alt.Theta('count:Q', title='Logs count'),
    alt.Color('sourcetype:N', title='Log sourcetype',sort=alt.SortField(field='count', order='descending')),
).properties(
    width=600,
    height=500,
    title='24 hours DT-Splunk host Logs count per sourcetype'
)
pie_chart

In [ ]:
hosts = pd.read_csv('last_2_weeks_hosts.csv')

In [ ]:
hosts.host = hosts.host.str.lower()
hosts.sort_values('host', ascending=True)
# cancel show all the df config
alt.data_transformers.disable_max_rows()




In [ ]:
df.user.unique()

In [ ]:
df = pd.read_csv('host_host_type_user_24h.csv')
df = df[df.host_type=='dt']
chart = alt.Chart(df).mark_bar().encode(
    alt.Color('host:N', title='host'),
    alt.Y('count:Q', title='Logs count'),
    alt.X('user:N', title='user_name',sort=alt.SortField(field='host_type', order='descending')),
).properties(
    width=2500,
    height=600,
    title='hosts'
).configure_axis(
    labelFontSize=15,
    titleFontSize=20,
    labelAngle=45
).configure_legend(
    labelFontSize=15
)
chart

In [ ]:
df = pd.read_csv('source_host_type_user_24h.csv')
df = df[df.host_type=='dt']
chart = alt.Chart(df).mark_bar().encode(
    alt.Color('source:N', title='host'),
    alt.Y('count:Q', title='Logs count'),
    alt.X('user:N', title='user_name',sort=alt.SortField(field='host_type', order='descending')),
).properties(
    width=2500,
    height=600,
    title='hosts'
).configure_axis(
    labelFontSize=15,
    titleFontSize=20,
    labelAngle=45
).configure_legend(
    labelFontSize=15
)
chart

In [ ]:
df = pd.read_csv('host_type_host_24h.csv')
chart = alt.Chart(df).mark_bar().encode(
    alt.Color('host_type:N', title='host_type'),
    alt.Y('count:Q', title='Logs count'),
    alt.X('host:N', title='host',sort=alt.SortField(field='host_type', order='descending')),
).properties(
    width=2500,
    height=600,
    title='hosts'
).configure_axis(
    labelFontSize=15,
    titleFontSize=20,
    labelAngle=45
).configure_legend(
    labelFontSize=15
)
chart

In [ ]:
df = pd.read_csv('host_type_source_24h.csv')
chart = alt.Chart(df).mark_bar().encode(
    alt.X('host_type:N', title='host_type'),
    alt.Y('count:Q', title='Logs count'),
    alt.Color('source:N', title='source'),
).properties(
    width=800,
    height=600,
    title='hosts sources'
).configure_axis(
    labelFontSize=15,
    titleFontSize=20,
    labelAngle=45
).configure_legend(
    labelFontSize=15,
    labelLimit=10000
)
chart